- tip4p water
- opls alcohols

# setup

## import stuff

In [ ]:
# magics
%matplotlib inline

# regulary used
from copy import deepcopy
import glob
import matplotlib as mpl
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
import numpy as np
import os
import pandas as pd
import pickle
import re
import tempfile
from scipy import constants as const
from scipy import integrate
from scipy import optimize
import xml.etree.ElementTree as ET

# from own toolbox
import gromacstools as gt
run_bash = gt.general.run_bash
WorkingDir = gt.general.WorkingDir

# own constants
const.k_gro = const.k * const.N_A * 1e-3
const.h_gro = const.h * const.N_A * 1e-3 * 1e12
const.rec_cm_per_THz = 1e12 / const.c / 100
const.bar_per_md_pressure = 10**28 * const.u

# notebook wide variables
jobids = []

In [ ]:
np.append([1, 2, 3], 4)

## notebook specific constants

In [ ]:
project_label = "23-implicit-ihnc"

remote_host = "franklin"
remote_dir_base = os.path.join("/scratch-enzo/mbernhardt/run", project_label)

## systems

In [ ]:
atomtypes = {'O': {'name': 'O', 'mass': 15.9994},
             'H': {'name': 'H', 'mass':  1.008},
             'M': {'name': 'M', 'mass':  0.0},
             'C': {'name': 'C', 'mass': 12.01100}}

water_atoms = [atomtypes[atom] for atom in ['O', 'H', 'H', 'M']]
methanol_atoms = [atomtypes[atom] for atom in ['C', 'H', 'H', 'H', 'O', 'H', 'M']]
ethanol_atoms = [atomtypes[atom] for atom in ['C', 'H', 'H', 'H', 'C', 'H', 'H', 'O', 'H', 'M']]
propanol_atoms = [atomtypes[atom] for atom in ['C', 'H', 'H', 'H', 'C', 'H', 'H', 'C', 'H', 'H', 'O', 'H', 'M']]

water_moltypes = [{'name': "SOL", 'atoms': water_atoms, 'nmols': None,}]
methanol_moltypes = [{'name': "MET", 'atoms': methanol_atoms, 'nmols': None}]
ethanol_moltypes = [{'name': "ETH", 'atoms': ethanol_atoms, 'nmols': None}]
propanol_moltypes = [{'name': "POL", 'atoms': propanol_atoms, 'nmols': None}]

mixtures = {
    'tip4p-meoh': {'moltypes': deepcopy(water_moltypes + methanol_moltypes),
                   'cut_off': 1.2, 'g_end': 2.0, 'step': 0.005, 'systems': [],
                   'nmols': 8000, 'nmols_cg': 7200,
                   'mole_fractions': [0.05, 0.1, 0.2, 0.4, 0.6, 0.8, 0.9]}
}

systems = []
for mix_name, mix in mixtures.items():
    for x in mix['mole_fractions']:
        system_moltypes = deepcopy(mix['moltypes'])
        nmols_sol = int((1 - x) * mix['nmols'])
        nmols_alc = int(x * mix['nmols'])
        system_moltypes[0]['nmols'] = nmols_sol
        system_moltypes[1]['nmols'] = nmols_alc
        real_x = nmols_alc / (nmols_sol + nmols_alc)
        system = {'name': f"oplsaa-{mix_name}-x{x:.2f}", 'temperature': 273.15 + 25,
                  'moltypes': system_moltypes, 'tags': [], 'cut_off': mix['cut_off'],
                  'g_end': mix['g_end'], 'step': mix['step'], 'x': real_x}
        systems.append(system)
        mix['systems'].append(system)

def volume_from_rho_M_N(density, molar_mass, n_mols):
    """
    density in g/mL
    molar_mass in g/mol
    n_mols
    """
    system_mass = n_mols * molar_mass / const.N_A  # in g
    volume = system_mass / density  # in mL
    return volume / 1e-21 # in nm³

# some additional fields for later use
for system_nr, system in enumerate(systems):
    top = gt.top.Topology()
    top.load_simple_top(system['moltypes'])
    system['top'] = top
    nmols = system['top'].nmols()
    molar_mass = sum((mol.mass for mol in top.mols())) / nmols
    density_init = 1.0
    system['volume_init'] = volume_from_rho_M_N(density_init, molar_mass, nmols)
    
# print systems
pd.DataFrame(systems)

## osmp_methods, cg_methods, fit-function

In [ ]:
osmp_methods = {#'osmp-z-k500': {'k': 500, 'scale': 'z'},
                #'osmp-z-k4000': {'k': 4000, 'scale': 'z'},
                'osmp-xy-k500': {'k': 500, 'scale': 'xy'},
                'osmp-xy-k4000': {'k': 4000, 'scale': 'xy'}}
"""osmp_methods = {'osmp-xy-k500': {'k': 500, 'scale': 'xy'},
                'osmp-xy-k4000': {'k': 4000, 'scale': 'xy'}}"""
for osmp_name in osmp_methods:
    print(osmp_name)

In [ ]:
cg_methods = [{'name': 'hncgn-1', 'method': 'hncgn', 'p-constr': None, 'init': 'hnc'},
              {'name': 'hncgn-2', 'method': 'hncgn', 'p-constr': None, 'init': 'bi'},
              {'name': 'p-hncgn-1', 'method': 'hncgn', 'p-constr': 'osmp', 'init': 'hnc'}, 
              {'name': 'p-hncgn-2', 'method': 'hncgn', 'p-constr': 'osmp', 'init': 'hnc'},
              {'name': 'p-hncgn-3', 'method': 'hncgn', 'p-constr': 'osmp', 'init': 'hnc'},
              {'name': 'p-hncgn-4', 'method': 'hncgn', 'p-constr': 'osmp', 'init': 'hnc'}]
for cg_method in cg_methods:
    print(cg_method['name'])

In [ ]:
def fx3(x, a, b, c):
    return a*x**3 + b*x**2 + c*x

def fx4(x, a, b, c, d):
    return a*x**4 + b*x**3 + c*x**2 + d*x

In [ ]:
transf_tempf = [0.9, 1.0, 1.1]
transf_cg_methods = cg_methods[0:1] + cg_methods[2:3]
print(transf_tempf)

## often used functions

In [ ]:
def readin_table(filename):
    data = np.loadtxt(filename, dtype=np.str, comments=['#', '@'])
    x = data[:, 0].astype(np.float)
    y = data[:, 1].astype(np.float)
    y_flag = data[:, 2].astype('S1')
    return x, y, y_flag

In [ ]:
def check_job_stati(jobids, remote_host):
    stati = gt.remote.check_slurm_jobs(jobids, remote_host)

    # print status for each job
    completed_jobids = []
    for jobid, status in zip(jobids, stati):
        print(jobid, status)
        if (status in ('FAILED', 'COMPLETED', None)
            or status.startswith('CANCELLED')):
            completed_jobids.append(jobid)

    # remove jobids which are completed
    new_jobids = [jobid for jobid in jobids if jobid not in completed_jobids]
    return new_jobids

# MD NPT all-atom

## prepare md

In [ ]:
template_dir = os.path.abspath('template')

for system in systems:
    print("system", system['name'])
          
    with WorkingDir(system['name']):
        # make dirs and copy template files
        run_bash("mkdir -p topol equi1 equi2 equi3 equi4 prod")
        for moltype in system['moltypes']:
            moltype_name = moltype['name']
            run_bash(f"cp {template_dir}/oplsaa/{moltype_name}/moleculetype.itp topol/{moltype_name}.itp")
            run_bash(f"cp {template_dir}/oplsaa/{moltype_name}/single.gro equi1/{moltype_name}-single.gro")
            
        run_bash(f"cp {template_dir}/oplsaa/forcefield.itp topol/forcefield.itp")
        run_bash(f"cp {template_dir}/oplsaa/ffnonbonded.itp topol/ffnonbonded.itp")
        run_bash(f"cp {template_dir}/oplsaa/ffbonded.itp topol/ffbonded.itp")
        run_bash(f"cp {template_dir}/md-npt/equi1.mdp equi1/grompp.mdp")
        run_bash(f"cp {template_dir}/md-npt/equi2.mdp equi2/grompp.mdp")
        run_bash(f"cp {template_dir}/md-npt/equi3.mdp equi3/grompp.mdp")
        run_bash(f"cp {template_dir}/md-npt/equi4.mdp equi4/grompp.mdp")
        run_bash(f"cp {template_dir}/md-npt/prod.mdp prod/grompp.mdp")

        # run length
        gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',   5000)
        gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps',  10000)
        gt.mdp.set_parameter("equi3/grompp.mdp", 'nsteps', 100000)
        gt.mdp.set_parameter("equi4/grompp.mdp", 'nsteps', 500000)
        prod_run_length = int(8000 / system['top'].moltypes()[1].nmols * 200000)
        gt.mdp.set_parameter("prod/grompp.mdp",  'nsteps', prod_run_length)
        
        # set temperature
        gt.mdp.set_parameter("equi1/grompp.mdp", 'ref-t', system['temperature'])
        gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', system['temperature'])
        gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-t', system['temperature'])
        gt.mdp.set_parameter("equi4/grompp.mdp", 'ref-t', system['temperature'])
        gt.mdp.set_parameter("prod/grompp.mdp",  'ref-t', system['temperature'])
        
        # generate topol.top
        system_name = system['name']
        molecules = ""
        includes = ""
        for moltype in system['moltypes']:
            includes += '#include "' + moltype['name'] + '.itp"\n'
            molecules += moltype['name'] + ' ' + str(moltype['nmols']) + '\n'
        with open("topol/topol.top", 'w') as f:
            topol = f"""#include "forcefield.itp"
{includes}

[ system ]
{system_name}

[ molecules ]
{ molecules }
"""
            f.write(topol)
            
        
        # topol/???-map.xml and topol/settings.xml for RDF
        for moltype in system['moltypes']:
            moltype_name = moltype['name']
            if moltype_name == 'SOL':
                run_bash(f"cp {template_dir}/oplsaa/{moltype_name}/map.xml topol/{moltype_name}-map.xml")
            else:
                run_bash(f"cp {template_dir}/oplsaa/{moltype_name}/map.xml topol/ALC-map.xml")
        run_bash(f"cp {template_dir}/settings-rdf.xml topol/settings.xml")
        tree = ET.parse('topol/settings.xml')
        root = tree.getroot()
        root.find('non-bonded').find('max').text = str(system['g_end'])
        root.find('non-bonded').find('step').text = str(system['step'])
        tree.write('topol/settings.xml')
       

## fill box

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    working_dir = os.path.join(system['name'], 'equi1')
    
    scale = 0.6
          
    with WorkingDir(working_dir):
        box_edge = system['volume_init']**(1/3) * 1.1
          
        # insert molecules of the moltypes
        for moltype_nr, moltype in enumerate(system['moltypes']):
            moltype_name = moltype['name']
            moltype_nmols = moltype['nmols']
            if moltype_nr == 0:
                run_bash(f"gmx insert-molecules -box {box_edge} {box_edge} {box_edge} "
                         f"-ci {moltype_name}-single.gro -nmol {moltype_nmols} -o conf.gro "
                         f"-try 300 -scale {scale}")
            else:
                run_bash(f"gmx insert-molecules -f conf.gro "
                         f"-ci {moltype_name}-single.gro -nmol {moltype_nmols} -o conf.gro "
                         f"-try 300 -scale {scale}")
        run_bash("rm -f \#*")

        n_atoms_inserted = gt.gro.get_natoms("conf.gro")
        n_atoms_wanted = system['top'].natoms()
        if n_atoms_inserted != n_atoms_wanted:
            print(n_atoms_inserted, n_atoms_wanted)
            raise Exception("not enough molecules inserted")
            

## generate special tpr for partial xtc

In [ ]:
for system in systems:
    print("system", system['name'])
          
    with WorkingDir(system['name']):
        # special.gro
        top = deepcopy(system['top'])
        top.load_gro_file_pos_vel("equi1/conf.gro")
        del top.distinctive_top[0]
        top.save_gro_file("special.gro", [10, 10, 10])
        
        # special.top
        molecules = ""
        includes = ""
        for moltype in system['moltypes'][1:2]:
            includes += '#include "' + moltype['name'] + '.itp"\n'
            molecules += moltype['name'] + ' ' + str(moltype['nmols']) + '\n'
        with open("topol/special.top", 'w') as f:
            topol = f"""#include "forcefield.itp"
{includes}

[ system ]
special

[ molecules ]
{ molecules }
"""
            f.write(topol)
            
        # special.tpr
        run_bash("gmx grompp -f equi1/grompp.mdp -p topol/special.top -c special.gro -o topol/special.tpr -maxwarn 1")
        run_bash("rm -f special.gro topol/special.top")

## md on cluster

In [ ]:
for system in systems:
    
    print(f"system {system['name']}")
    remote_dir = os.path.join(remote_dir_base, system['name'])

    with WorkingDir(system['name']):
        # mkdir
        run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

        # copy simulation files to remote
        filelist = ["equi1 equi2 equi3 equi4 prod topol"]
        gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

        # commands to be run on compute nodes
        script = """#!/bin/bash
#SBATCH --job-name=md
#SBATCH --exclusive
#SBATCH --time=48:00:00
#SBATCH --partition=enzo

set -eo pipefail
shopt -s expand_aliases
alias gmx="gmx -quiet"

module purge
spack load /qmpnnzb  # gromacs@2019.5 ~mpi simd=SSE2
spack load /e4wa6u5  # fftw@3.3.8~mpi~openmp~pfft_patches precision=double,float
spack load /p2rbc3m  # boost@1.72~python
source /home/mbernhardt/software/votca/bin/VOTCARC.bash
source /home/mbernhardt/software/miniconda3/etc/profile.d/conda.sh
conda activate

pushd equi1
#gmx grompp -p ../topol/topol.top
#gmx mdrun
rm -f \#*
popd

pushd equi2
#gmx grompp -p ../topol/topol.top -c ../equi1/confout.gro
#gmx mdrun
rm -f \#*
popd

pushd equi3
#gmx grompp -p ../topol/topol.top -c ../equi2/confout.gro
#gmx mdrun
rm -f \#*
popd

pushd equi4
#gmx grompp -p ../topol/topol.top -c ../equi3/confout.gro
#gmx mdrun
rm -f \#*
popd

pushd prod
gmx grompp -p ../topol/topol.top -c ../equi4/confout.gro
gmx mdrun -x $JOBTMP/traj_comp.xtc
rm -f \#*
popd

ls -lh $JOBTMP

pushd prod
csg_stat --top ../topol/special.tpr --options ../topol/settings.xml --trj $JOBTMP/traj_comp.xtc \
--cg "../topol/ALC-map.xml;../topol/SOL-map.xml" --nt=24
rm -f \#*
popd

rm -f $JOBTMP/*
"""

        jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
        print(jobid)
        if jobid != None:
            jobids.append(jobid)

## check job status

In [ ]:
# print status for each job
completed_jobids = []
for jobid in jobids:
    stati = gt.remote.check_slurm_job(jobid, remote_host)
    print(jobid, stati)
    if stati[-1] in ('FAILED', 'COMPLETED', 'CANCELLED', None):
        completed_jobids.append(jobid)

# remove jobids which are completed
jobids = [jobid for jobid in jobids if jobid not in completed_jobids]

## copy results from cluster

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    remote_dir = os.path.join(remote_dir_base, system['name'])

    with WorkingDir(system['name']):
        exclude = "traj*"
        #filelist = ["*/*.edr", "prod/*.dist.new*", "*/confout.gro", "*/topol.tpr"]
        filelist = ["*/*.edr", "*/confout.gro", "*/topol.tpr", "prod/A-A.dist.new"]
        gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)

## equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in systems:
    print(f"system {system['name']}")
          
    with WorkingDir(system['name']):
        #print("equilibration 2")
        #show_energy_graphs(["Temperature"], edr_file="equi2/ener.edr")
        #print("equilibration 3")
        #show_energy_graphs(["Temperature", "Volume"], edr_file="equi3/ener.edr")
        print("production")
        show_energy_graphs(["Temperature", "Volume"], edr_file="prod/ener.edr")
        #print("production 2")
        #show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")
        #show_energy_graphs(["Temperature", "Volume"], edr_file="prod2/ener.edr")
        #show_energy_graphs(["Pressure"], edr_file="prod/ener.edr")

## determine concentration

In [ ]:
for system in systems:
    print(f"system {system['name']}")
          
    with WorkingDir(system['name']):
        run_bash("gmx energy -f prod/ener.edr -o energy-temp.xvg <<< 'volume'")
        data, header = gt.xvg.load("energy-temp.xvg")
        run_bash("rm energy-temp.xvg")
        volume = np.mean(data['Volume']) / 1e27 * 1e3  # in liter
        amount1 = system['moltypes'][1]['nmols'] / const.N_A  # in mole
        concentration1 = amount1 / volume  # in mole/liter
        print(concentration1)
        osmotic_pressure_est = concentration1 * const.R * system['temperature']  # in J/liter
        osmotic_pressure_est *= 1000 / 1e5  # in bar
        print(osmotic_pressure_est)

## show RDFs

In [ ]:
for mix_name, mix in mixtures.items():
    
    fig, ax = plt.subplots()
    axins = inset_axes(ax, width="50%", height="40%", loc='lower right')
    axins2 = inset_axes(ax, width="40%", height="30%", loc='upper right')
    for system in mix['systems']:
        print(f"system {system['name']}")
              
        with WorkingDir(system['name']):
            data, header = gt.xvg.load("prod/A-A.dist.new")
            ax.plot(data[0], data[1], label=f"{system['x']:.2f}")
            axins.plot(data[0], data[1])
            axins2.plot(data[0], data[1])
    
    ax.legend(title='x(' + system['moltypes'][1]['name'] + ')', loc='lower left')
    ax.set_xlim(0, system['g_end'])
    ax.set_ylim(bottom=0)
    axins.set_xlim(0.3, 0.5)
    axins.set_ylim(0.6, 1.75)
    axins2.set_xlim(0.6 * system['g_end'], 1.01 * system['g_end'])
    axins2.set_ylim(0.995, 1.005)
    #fig.tight_layout()
    ax.set_xlabel("r in nm")
    ax.set_ylabel("g(r)")
    fig.savefig(f"figures/rdf-{mix_name}.png", dpi=150)
    plt.show()

# osmotic pressure MD

## prepare osmotic pressure md

In [ ]:
for osmp_name, osmp_method in osmp_methods.items():
    print(osmp_name, osmp_method)

In [ ]:
template_dir = os.path.abspath('template')

for system in systems:
    print("system", system['name'])
          
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        
        with WorkingDir(system['name'] + "/" + osmp_name):
            # make dirs and copy template files
            run_bash("mkdir -p topol equi1 equi2 equi3 equi4 pre equi5 prod")
            for i, moltype in enumerate(system['moltypes']):
                moltype_name = moltype['name']
                run_bash(f"cp {template_dir}/oplsaa/{moltype_name}/single.gro equi1/{moltype_name}-single.gro")
                if i == 0:
                    run_bash(f"cp {template_dir}/oplsaa/{moltype_name}/moleculetype.itp topol/{moltype_name}.itp")
                else:
                    run_bash(f"cp {template_dir}/oplsaa/{moltype_name}/moleculetype.itp topol/{moltype_name}-unrestr.itp")

            run_bash(f"cp {template_dir}/oplsaa/forcefield.itp topol/forcefield.itp")
            run_bash(f"cp {template_dir}/oplsaa/ffnonbonded.itp topol/ffnonbonded.itp")
            run_bash(f"cp {template_dir}/oplsaa/ffbonded.itp topol/ffbonded.itp")
            run_bash(f"cp {template_dir}/{osmp_name}/equi1.mdp equi1/grompp.mdp")
            run_bash(f"cp {template_dir}/{osmp_name}/equi2.mdp equi2/grompp.mdp")
            run_bash(f"cp {template_dir}/{osmp_name}/equi3.mdp equi3/grompp.mdp")
            run_bash(f"cp {template_dir}/{osmp_name}/equi4.mdp equi4/grompp.mdp")
            run_bash(f"cp {template_dir}/{osmp_name}/pre.mdp pre/grompp.mdp")
            run_bash(f"cp {template_dir}/{osmp_name}/equi5.mdp equi5/grompp.mdp")
            run_bash(f"cp {template_dir}/{osmp_name}/prod.mdp prod/grompp.mdp")

            # copy confout from NPT prod
            run_bash(f"cp ../prod/confout.gro equi1/npt-confout.gro")

            # run length
            gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',    5000)
            gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps',   10000)
            gt.mdp.set_parameter("equi3/grompp.mdp", 'nsteps',  100000)
            gt.mdp.set_parameter("equi4/grompp.mdp", 'nsteps',  400000)
            gt.mdp.set_parameter("pre/grompp.mdp",   'nsteps',  400000)
            gt.mdp.set_parameter("equi5/grompp.mdp", 'nsteps', 1000000)
            gt.mdp.set_parameter("prod/grompp.mdp",  'nsteps',  400000)

            # set temperature
            gt.mdp.set_parameter("equi1/grompp.mdp", 'ref-t', system['temperature'])
            gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', system['temperature'])
            gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-t', system['temperature'])
            gt.mdp.set_parameter("equi4/grompp.mdp", 'ref-t', system['temperature'])
            gt.mdp.set_parameter("pre/grompp.mdp",   'ref-t', system['temperature'])
            gt.mdp.set_parameter("equi5/grompp.mdp", 'ref-t', system['temperature'])
            gt.mdp.set_parameter("prod/grompp.mdp",  'ref-t', system['temperature'])

            # set pre-run pressure
            pre_p = 1000.0
            if osmp_method['scale'] == 'z':
                gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-p', "0.0 " + str(pre_p))
                gt.mdp.set_parameter("equi4/grompp.mdp", 'ref-p', "0.0 " + str(pre_p))
                gt.mdp.set_parameter("pre/grompp.mdp",   'ref-p', "0.0 " + str(pre_p))
            elif osmp_method['scale'] == 'xy':
                gt.mdp.set_parameter("equi3/grompp.mdp", 'ref-p', str(pre_p) + " 0.0")
                gt.mdp.set_parameter("equi4/grompp.mdp", 'ref-p', str(pre_p) + " 0.0")
                gt.mdp.set_parameter("pre/grompp.mdp",   'ref-p', str(pre_p) + " 0.0")

## elongate and fill box, create osmp_system

In [ ]:
# insert scale
scale = 0.57
    
def N_from_rho_M_V(density, molar_mass, volume):
    """
    density in g/mL
    molar_mass in g/mol
    volume in nm^3
    """
    # m = V * ρ
    mass = (volume / 1e21) * density # in g
    # n = m / M
    amount_of_substance = mass / molar_mass # in mol
    return amount_of_substance * const.N_A  # in entities

for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name, 'equi1')
          
        with WorkingDir(working_dir):
            if osmp_nr == 0:
                box_edge, _, _ = gt.gro.get_box('npt-confout.gro')

                # partially enlarge box
                run_bash(f"gmx editconf -f npt-confout.gro -box {box_edge} {box_edge} {box_edge*2-0.4} -o elongated.gro")

                # insert water molecules
                new_moltype = system['moltypes'][0]
                new_name = new_moltype['name']
                new_mass = system['top'].mols()[0].mass
                new_volume = box_edge**3  # total minus center slab
                # density of water = 1 g/ml
                new_nmols = int(N_from_rho_M_V(1.0, new_mass, new_volume))
                run_bash(f"gmx insert-molecules -f elongated.gro "
                         f"-ci {new_name}-single.gro -nmol {new_nmols} -o inserted.gro "
                         f"-try 300 -scale {scale}")
                run_bash("rm -f \#*")

                n_atoms_inserted = gt.gro.get_natoms("inserted.gro")
                n_atoms_wanted = system['top'].natoms() + new_nmols * len(new_moltype['atoms'])
                if n_atoms_inserted != n_atoms_wanted:
                    print(n_atoms_inserted, n_atoms_wanted)
                    raise Exception("not enough molecules inserted")

                # fully enlarge box
                run_bash(f"gmx editconf -f inserted.gro -box {box_edge} {box_edge} {box_edge*2} -o conf.gro")
                run_bash(f"rm -f elongated.gro inserted.gro")

                # osmotic pressure system
                osmp_system = deepcopy(system)
                osmp_system['name'] += '/' + osmp_name
                # moltypes with new mols
                osmp_moltypes = osmp_system['moltypes']
                osmp_moltypes.append(deepcopy(osmp_moltypes[0]))
                osmp_moltypes[-1]['nmols'] = new_nmols
                osmp_system['moltypes'] = osmp_moltypes
                # topology
                osmp_top = gt.top.Topology()
                osmp_top.load_simple_top(osmp_moltypes)
                osmp_system['top'] = osmp_top
                # link in reference system
                system['osmp_system'] = osmp_system
                # write to file
                with open("../osmp_system.pkl", 'wb') as f:
                    pickle.dump(osmp_system, f)
            else:
                run_bash(f"cp ../../{list(osmp_methods.keys())[0]}/equi1/conf.gro conf.gro")
                run_bash(f"cp ../../{list(osmp_methods.keys())[0]}/osmp_system.pkl ../osmp_system.pkl")

## prepare restraint itp, topol.top and restraints.gro

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            with open("osmp_system.pkl", 'rb') as f:
                osmp_system = pickle.load(f)
        
            # generate *.itp
            solute_name = osmp_system['moltypes'][1]['name']
            box_edge, _, _ = gt.gro.get_box('equi1/npt-confout.gro')
            restr_r = box_edge / 2
            restr_center = np.round(box_edge, 3)  # precision of restraints.gro file
            restr_k = osmp_method['k']
            run_bash(f"cp topol/{solute_name}-unrestr.itp topol/{solute_name}.itp")
            with open(f"topol/{solute_name}.itp", 'a') as f:
                topol = f"""
[ position_restraints ]
;ai  funct  g  r          k
7    2      5  {restr_r}  {restr_k}
"""
                f.write(topol)


            # generate topol.top
            system_name = osmp_system['name']
            molecules = ""
            includes = ""
            for mt_name in set([mt['name'] for mt in osmp_system['moltypes']]):
                includes += '#include "' + mt_name + '.itp"\n'
            for moltype in osmp_system['moltypes']:
                molecules += moltype['name'] + ' ' + str(moltype['nmols']) + '\n'
            with open("topol/topol.top", 'w') as f:
                topol = f"""#include "forcefield.itp"
{includes}

[ system ]
{system_name}

[ molecules ]
{ molecules }
"""
                f.write(topol)


            # generate restraints.gro
            run_bash(f"cp equi1/conf.gro topol/restraint.gro")
            top = osmp_system['top']
            # load gro file
            top.load_gro_file_pos_vel("topol/restraint.gro")
            box = gt.gro.get_box("topol/restraint.gro")
            # modify coordinates
            for atom in top.moltypes()[0].atoms() + top.moltypes()[2].atoms():
                atom.pos = np.zeros(3)
            for atom in top.moltypes()[1].atoms():
                atom.pos = np.array([0.0, 0.0, restr_center])
            # save gro file
            top.save_gro_file("topol/restraint.gro", box)

## osmotic pressure pre-run

In [ ]:
for system in systems[:7]:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
        remote_dir = os.path.join(remote_dir_base, system['name'], osmp_name)
          
        with WorkingDir(working_dir):
          
            # wallforce parameters
            box_edge, _, _ = gt.gro.get_box('equi1/npt-confout.gro')
            restr_r = box_edge / 2
            restr_center = np.round(box_edge, 3)  # precision of restraints.gro file
            wall_low = restr_center - restr_r
            wall_high = restr_center + restr_r
            restr_k = osmp_method['k']
            inner_wall_low = restr_center - 0.5*restr_r
            inner_wall_high = restr_center + 0.5*restr_r

            # mkdir
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

            # copy simulation files to remote
            filelist = ["equi1 equi2 equi3 equi4 pre topol"]
            gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

            # commands to be run on compute nodes
            script = fr"""#!/bin/bash
#SBATCH --job-name=osmp-md
#SBATCH --exclusive
#SBATCH --time=96:00:00
#SBATCH --partition=enzo

set -euo pipefail
shopt -s expand_aliases
alias gmx="gmx -quiet"

module purge
spack load gromacs@2019 ~mpi simd=SSE2

pushd equi1
#gmx grompp -p ../topol/topol.top -r ../topol/restraint.gro
#gmx mdrun
rm -f \#*
popd

pushd equi2
#gmx grompp -p ../topol/topol.top -r ../topol/restraint.gro -c ../equi1/confout.gro
#gmx mdrun
rm -f \#*
popd

pushd equi3
#gmx grompp -p ../topol/topol.top -r ../topol/restraint.gro -maxwarn 1 -c ../equi2/confout.gro
#gmx mdrun
rm -f \#*
popd

pushd equi4
#gmx grompp -p ../topol/topol.top -r ../topol/restraint.gro -maxwarn 1 -c ../equi3/confout.gro
#gmx mdrun
rm -f \#*
popd

pushd pre
#gmx grompp -p ../topol/topol.top -r ../topol/restraint.gro -maxwarn 1 -c ../equi4/confout.gro
#gmx mdrun
rm -f \#*
popd

pushd pre
#$HOME/bin/wallforce -quiet -f traj_comp.xtc -s topol.tpr -axis zn -wallr {wall_low} -wallk {restr_k} -o wallf-low.xvg <<< "name M"
#$HOME/bin/wallforce -quiet -f traj_comp.xtc -s topol.tpr -axis z -wallr {wall_high} -wallk {restr_k} -o wallf-high.xvg <<< "name M"
rm -f \#*
popd

pushd pre
echo -e 'atomname M and z > {wall_low} and z < {wall_high}\n'\
        'res_com of resname SOL and z > {wall_low} and z < {wall_high}'\
 | gmx select -f traj_comp.xtc -s topol.tpr -os size.xvg
rm -f \#*
popd

pushd pre
echo -e 'atomname M and z > {inner_wall_low} and z < {inner_wall_high}\n'\
        'res_com of resname SOL and z > {inner_wall_low} and z < {inner_wall_high}'\
  | gmx select -f traj_comp.xtc -s topol.tpr -os size-inner.xvg
rm -f \#*

"""

            jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)

## check job status

In [ ]:
# print status for each job
completed_jobids = []
for jobid in jobids:
    stati = gt.remote.check_slurm_job(jobid, remote_host)
    print(jobid, stati)
    if stati[-1] in ('FAILED', 'COMPLETED', 'CANCELLED', None):
        completed_jobids.append(jobid)

# remove jobids which are completed
jobids = [jobid for jobid in jobids if jobid not in completed_jobids]

## copy results from cluster

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
        remote_dir = os.path.join(remote_dir_base, system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            exclude = "traj*"
            filelist = ["*/*.edr", "*/confout.gro", "*/topol.tpr", "*/wallf-*.xvg", "*/size*.xvg"]
            gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)

## equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
        remote_dir = os.path.join(remote_dir_base, system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            #print("equilibration 2")
            #show_energy_graphs(["Temperature"], edr_file="equi2/ener.edr")
            print("equilibration 3")
            show_energy_graphs(["Temperature", "Volume", "Pres-XX"], edr_file="equi3/ener.edr")
            #print("equilibration 4")
            #show_energy_graphs(["Temperature", "Volume"], edr_file="equi4/ener.edr")
            #print("pre-run")
            #show_energy_graphs(["Temperature", "Volume"], edr_file="pre/ener.edr")

## create DataFrames

In [ ]:
# build empty DataFrame
iterables = [[system['name'] for system in systems],
             [osmp_name for osmp_name in osmp_methods],
             ['pre', 'prod']]
index = pd.MultiIndex.from_product(iterables, names=['system', 'osmp_method', 'run'])
df = pd.DataFrame(index=index, columns=["Pi_low", "Pi_high", "Pi_low_err", "Pi_high_err", "x", "x_err", "x_inner", "x_inner_err", "p_tot", "p_ex", "p_in"], dtype=np.float64)
df.head()

In [ ]:
# build empty DataFrame for fits
iterables = [['pre', 'prod'],
             [osmp_name for osmp_name in osmp_methods] + ['both']]
index = pd.MultiIndex.from_product(iterables, names=['run', 'osmp_method'])
df_fit = pd.DataFrame(index=index, columns=["fx3", "fx4"])
df_fit

## integrate wall force

In [ ]:
# f: force
# A: area
# Pi: osmotic pressure
# high, low: respective walls
    
n_blocks = 10

for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            if osmp_method['scale'] == 'z':
                box_x, box_y, _ = gt.gro.get_box('pre/confout.gro')
                A = box_x * box_y
            elif osmp_method['scale'] == 'xy':
                run_bash("gmx energy -f pre/ener.edr -o box-xy.xvg <<< 'Box-x\nBox-y'")
                data, _ = gt.xvg.load('box-xy.xvg')
                run_bash("rm box-xy.xvg")
                data['A'] = data['Box-X'] * data['Box-Y']
                A = data['A'].mean()
          
            data_low, header_low = gt.xvg.load("pre/wallf-low.xvg")
            data_high, header_high = gt.xvg.load("pre/wallf-high.xvg")
            #f_low_raw = np.abs(data_low['y'][data_low['Time (ps)'] > equi_time])
            #f_high_raw = np.abs(data_high['y'][data_high['Time (ps)'] > equi_time])
            f_low_raw = np.abs(data_low['y'])
            f_high_raw = np.abs(data_high['y'])
            len_block = len(f_low_raw) // n_blocks
            f_low_blocks = []
            f_high_blocks = []
            for i in range(n_blocks):
                f_low_blocks.append(np.mean(f_low_raw[len_block*i:len_block*(i+1)]))
                f_high_blocks.append(np.mean(f_high_raw[len_block*i:len_block*(i+1)]))
            f_low = np.mean(f_low_blocks)
            f_high = np.mean(f_high_blocks)
            f_low_err = np.std(f_low_blocks)
            f_high_err = np.std(f_high_blocks)
            Pi_low = f_low / A * const.bar_per_md_pressure
            Pi_high = f_high / A * const.bar_per_md_pressure
            Pi_low_err = f_low_err / A * const.bar_per_md_pressure
            Pi_high_err = f_high_err / A * const.bar_per_md_pressure
            #print(Pi_low, Pi_low_err)
            #print(Pi_high, Pi_high_err)
            #print(Pi_low_err, np.std(f_low_raw) / A * const.bar_per_md_pressure)
            df['Pi_low'][(system['name'], osmp_name, 'pre')] = Pi_low
            df['Pi_high'][(system['name'], osmp_name, 'pre')] = Pi_high
            df['Pi_low_err'][(system['name'], osmp_name, 'pre')] = Pi_low_err
            df['Pi_high_err'][(system['name'], osmp_name, 'pre')] = Pi_high_err

            fig, ax = plt.subplots(figsize=(10, 4))
            x = data_low['Time (ps)']
            ax.plot(x, data_low['y'])
            ax.plot(x, -data_high['y'])
            #x = np.arange(len_block/2, len_block*n_blocks, len_block) * data_low['Time (ps)'][1] + equi_time
            x = np.arange(len_block/2, len_block*n_blocks, len_block) * data_low['Time (ps)'][1]
            ax.plot(x, f_low_blocks)
            ax.plot(x, f_high_blocks)
            #ax.axvline(equi_time)
            plt.show()

In [ ]:
df.loc[(slice(None), slice(None), 'pre'), :]

## get p_tot (Pres-XX, Pres-YY)

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            run_bash("gmx energy -f pre/ener.edr -o pressure.xvg <<< 'Pres-XX\nPres-YY'")
            data, _ = gt.xvg.load('pressure.xvg')
            run_bash("rm pressure.xvg")
            p_tot = 1/2 * (data['Pres-XX'].mean() + data['Pres-YY'].mean())
            df['p_tot'][(system['name'], osmp_name, 'pre')] = p_tot

## calc p_in and p_ex

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            p_tot = df['p_tot'][(system['name'], osmp_name, 'pre')]
            Pi_low = df['Pi_low'][(system['name'], osmp_name, 'pre')]
            Pi_high = df['Pi_high'][(system['name'], osmp_name, 'pre')] 
            Pi = (Pi_low + Pi_high) / 2
            # p_tot = p_in + p_ex
            # Pi = p_in - p_ex
            p_ex = 1/2 * (p_tot - Pi)
            p_in = p_ex + Pi
            df['p_ex'][(system['name'], osmp_name, 'pre')] = p_ex
            df['p_in'][(system['name'], osmp_name, 'pre')] = p_in

## calculate actual mole fraction

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            data, header = gt.xvg.load("pre/size.xvg")
            data.columns = ['t', 'MET', 'SOL']
            data['x'] = data['MET'] / (data['MET'] + data['SOL'])
            x = data['x'].mean()
            x_err = data['x'].std()

            df['x'][(system['name'], osmp_name, 'pre')] = x
            df['x_err'][(system['name'], osmp_name, 'pre')] = x_err
          
            # inner regime
            data, header = gt.xvg.load("pre/size-inner.xvg")
            data.columns = ['t', 'MET', 'SOL']
            data['x'] = data['MET'] / (data['MET'] + data['SOL'])
            x = data['x'].mean()
            x_err = data['x'].std()

            df['x_inner'][(system['name'], osmp_name, 'pre')] = x
            df['x_inner_err'][(system['name'], osmp_name, 'pre')] = x_err

## fit

In [ ]:
# fit osmp-xy-k500
# polyfit first, then f(x) = cx + bx² + ax³
for fit, fit_f, fit_n in [('fx3', fx3, 3), ('fx4', fx4, 4)]:
    for osmp_name in osmp_methods:
        rows = (slice(None), osmp_name, 'pre')
        x = df['x_inner'][rows]
        y = (df['Pi_low'][rows] + df['Pi_high'][rows]) / 2

        # leave out last point
        x = x[:-1]
        y = y[:-1]

        prefit_p = np.polyfit(x, y, fit_n)
        fit_p, _ = optimize.curve_fit(fit_f, x, y, p0=prefit_p[:-1])
        df_fit.loc[('pre', osmp_name), fit] = fit_p

## fit (both k values)

In [ ]:
# fit osmp-xy-k500
# polyfit first, then f(x) = cx + bx² + ax³
for fit, fit_f, fit_n in [('fx3', fx3, 3), ('fx4', fx4, 4)]:
    rows = (slice(None), slice(None), 'pre')
    x = df['x_inner'][rows]
    y = (df['Pi_low'][rows] + df['Pi_high'][rows]) / 2

    # leave out last point
    #x = x[:-1]
    #y = y[:-1]

    prefit_p = np.polyfit(x, y, fit_n)
    fit_p, _ = optimize.curve_fit(fit_f, x, y, p0=prefit_p[:-1])
    df_fit.loc[('pre', 'both'), fit] = fit_p

In [ ]:
df_fit

## plot

In [ ]:
cmap = plt.get_cmap('rainbow')

# Literature data: Kohns et al 2017, different methanol forcefield, different osm. pres. method
lit_x = [0.8779, 0.7901, 0.5098, 0.2235, 0.0407]
lit_x_err = [0.0008, 0.0008, 0.0007, 0.0004, 0.0001]
lit_y = [2180, 1409, 569, 258, 53.6]
lit_y_err = [5, 4, 4, 2, 0.9]

fig, ax = plt.subplots(figsize=(18, 8))
axins = inset_axes(ax, width="50%", height="40%", loc='upper left')
for i, osmp_name in enumerate(osmp_methods):
    for axi in [ax, axins]:
        rows = (slice(None), osmp_name, 'pre')
        #axi.errorbar(df['x'][rows], df['Pi_low'][rows], xerr=df['x_err'][rows], yerr=df['Pi_low_err'][rows],
                    #color=cmap(i/4), label=osmp_name + ' low')
        #axi.errorbar(df['x'][rows], df['Pi_high'][rows], xerr=df['x_err'][rows], yerr=df['Pi_high_err'][rows],
                    #color=cmap(i/4+0.1), label=osmp_name + ' high')
        axi.errorbar(df['x_inner'][rows], df['Pi_low'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_low_err'][rows],
                    color=cmap(i/4), label=osmp_name + ' low inner', linestyle='')
        axi.errorbar(df['x_inner'][rows], df['Pi_high'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_high_err'][rows],
                    color=cmap(i/4+0.1), label=osmp_name + ' high inner', linestyle='')
        x = df['x_inner'][rows]
        fit_x = np.arange(0, max(x), 0.01)
        #fit_y = fx3(fit_x, *df_fit.loc[('pre', osmp_name), 'fx3'])
        #axi.plot(fit_x, fit_y, color=cmap(i/4), linestyle='-.', zorder=10, label=osmp_name + ' fit pre')
        fit_y = fx4(fit_x, *df_fit.loc[('pre', osmp_name), 'fx4'])
        axi.plot(fit_x, fit_y, color=cmap(i/4), linestyle='-.', zorder=10, label=osmp_name + ' fit fx4 pre')
ax.errorbar(lit_x, lit_y, xerr=lit_x_err, yerr=lit_y_err, linestyle=':', label='Kohns et al')
axins.errorbar(lit_x, lit_y, xerr=lit_x_err, yerr=lit_y_err, linestyle=':', label='Kohns et al')
ax.legend()
ax.set_xlim(0)
ax.set_ylim(0)
axins.set_xlim(0, 0.2)
axins.set_ylim(0, 400)
#ax.set_xlim(0, 0.2)
#ax.set_ylim(0, 400)
plt.show()

In [ ]:
cmap = plt.get_cmap('rainbow')

fig, ax = plt.subplots(figsize=(10, 5))
for i, osmp_name in enumerate(osmp_methods):
    rows = (slice(None), osmp_name, 'pre')
    ax.errorbar(df['x'][rows], df['Pi_low'][rows], xerr=df['x_err'][rows], yerr=df['Pi_low_err'][rows],
                color=cmap(i/4), label=osmp_name + ' low', linestyle='')
    ax.errorbar(df['x'][rows], df['Pi_high'][rows], xerr=df['x_err'][rows], yerr=df['Pi_high_err'][rows],
                color=cmap(i/4), label=osmp_name + ' high', linestyle='')
    ax.plot(df['x'][rows], df['p_tot'][rows], color=cmap(i/4), label=osmp_name + ' p_tot', linestyle=':')
ax.legend()
ax.set_xlim(0)
ax.set_ylim(0)
plt.show()

## set production pressure

\begin{align}
p_{tot} &= p_{in} + p_{ex}\\
\Pi &= p_{in} - p_{ex}\\
p_{tot} &= 2 * p_{ex} + \Pi\\
p_{ex} &= 1 bar\\
%p_{ex} &= 1/2 * (p_{tot} - \Pi)\\
\end{align}
            

In [ ]:
for system in systems:
    print("system", system['name'])
          
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        
        with WorkingDir(system['name'] + "/" + osmp_name):
            row = (system['name'], osmp_name, 'pre')
            p_ex = 1.0
            Pi = 1/2 * (df['Pi_low'][row] + df['Pi_high'][row])
            p_tot = 2 * p_ex + Pi
            if osmp_method['scale'] == 'z':
                gt.mdp.set_parameter("equi5/grompp.mdp", 'ref-p', "0.0 " + str(p_tot))
                gt.mdp.set_parameter("prod/grompp.mdp",  'ref-p', "0.0 " + str(p_tot))
            elif osmp_method['scale'] == 'xy':
                gt.mdp.set_parameter("equi5/grompp.mdp", 'ref-p', str(p_tot) + " 0.0")
                gt.mdp.set_parameter("prod/grompp.mdp",  'ref-p', str(p_tot) + " 0.0")

## osmotic pressure production run

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
        remote_dir = os.path.join(remote_dir_base, system['name'], osmp_name)
          
        with WorkingDir(working_dir):
          
            # wallforce parameters
            box_edge, _, _ = gt.gro.get_box('equi1/npt-confout.gro')
            restr_r = box_edge / 2
            restr_center = np.round(box_edge, 3)  # precision of restraints.gro file
            wall_low = restr_center - restr_r
            wall_high = restr_center + restr_r
            restr_k = osmp_method['k']
            inner_wall_low = restr_center - 0.5*restr_r
            inner_wall_high = restr_center + 0.5*restr_r
            

            # mkdir
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

            # copy simulation files to remote
            filelist = ["equi5 prod topol"]
            gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

            # commands to be run on compute nodes
            script = fr"""#!/bin/bash
#SBATCH --job-name=osmp-md
#SBATCH --exclusive
#SBATCH --time=96:00:00
#SBATCH --partition=enzo

set -euo pipefail
shopt -s expand_aliases
alias gmx="gmx -quiet"

module purge
spack load gromacs@2019 ~mpi simd=SSE2

pushd equi5
gmx grompp -p ../topol/topol.top -r ../topol/restraint.gro -maxwarn 1 -c ../pre/confout.gro
gmx mdrun
rm -f \#*
popd

pushd prod
gmx grompp -p ../topol/topol.top -r ../topol/restraint.gro -maxwarn 1 -c ../equi5/confout.gro
gmx mdrun
rm -f \#*
popd

pushd prod
$HOME/bin/wallforce -quiet -f traj_comp.xtc -s topol.tpr -axis zn -wallr {wall_low} -wallk {restr_k} -o wallf-low.xvg <<< "name M"
$HOME/bin/wallforce -quiet -f traj_comp.xtc -s topol.tpr -axis z -wallr {wall_high} -wallk {restr_k} -o wallf-high.xvg <<< "name M"
rm -f \#*
popd

pushd prod
echo -e 'atomname M and z > {wall_low} and z < {wall_high}\n'\
        'res_com of resname SOL and z > {wall_low} and z < {wall_high}'\
  | gmx select -f traj_comp.xtc -s topol.tpr -os size.xvg
rm -f \#*
popd

pushd prod
echo -e 'atomname M and z > {inner_wall_low} and z < {inner_wall_high}\n'\
        'res_com of resname SOL and z > {inner_wall_low} and z < {inner_wall_high}'\
  | gmx select -f traj_comp.xtc -s topol.tpr -os size-inner.xvg
rm -f \#*

pushd prod
gmx density -f traj_comp.xtc -o density-1.xvg <<< "1"
gmx density -f traj_comp.xtc -o density-3.xvg <<< "3"
popd

"""

            jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)

## check job status

In [ ]:
# print status for each job
completed_jobids = []
for jobid in jobids:
    stati = gt.remote.check_slurm_job(jobid, remote_host)
    print(jobid, stati)
    if stati[-1] in ('FAILED', 'COMPLETED', 'CANCELLED', None):
        completed_jobids.append(jobid)

# remove jobids which are completed
jobids = [jobid for jobid in jobids if jobid not in completed_jobids]

## copy results from cluster

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
        remote_dir = os.path.join(remote_dir_base, system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            exclude = "traj*"
            filelist = ["*/*.edr", "*/confout.gro", "*/topol.tpr", "*/wallf-*.xvg", "*/size*.xvg"]
            gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)

## equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            print("equilibration 5")
            show_energy_graphs(["Temperature", "Volume", "Pres-XX"], edr_file="equi5/ener.edr")
            #print("production")
            #show_energy_graphs(["Temperature", "Volume"], edr_file="prod/ener.edr")

## integrate wall force

In [ ]:
# f: force
# A: area
# Pi: osmotic pressure
# high, low: respective walls
    
n_blocks = 10

for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            if osmp_method['scale'] == 'z':
                box_x, box_y, _ = gt.gro.get_box('prod/confout.gro')
            elif osmp_method['scale'] == 'xy':
                run_bash("gmx energy -f prod/ener.edr -o box-xy.xvg <<< 'Box-x\nBox-y'")
                data, _ = gt.xvg.load('box-xy.xvg')
                run_bash("rm box-xy.xvg")
                box_x = data['Box-X'].mean()
                box_y = data['Box-Y'].mean()
          
            A = box_x * box_y
            data_low, header_low = gt.xvg.load("prod/wallf-low.xvg")
            data_high, header_high = gt.xvg.load("prod/wallf-high.xvg")
            f_low_raw = np.abs(data_low['y'])
            f_high_raw = np.abs(data_high['y'])
            len_block = len(f_low_raw) // n_blocks
            f_low_blocks = []
            f_high_blocks = []
            for i in range(n_blocks):
                f_low_blocks.append(np.mean(f_low_raw[len_block*i:len_block*(i+1)]))
                f_high_blocks.append(np.mean(f_high_raw[len_block*i:len_block*(i+1)]))
            f_low = np.mean(f_low_blocks)
            f_high = np.mean(f_high_blocks)
            f_low_err = np.std(f_low_blocks)
            f_high_err = np.std(f_high_blocks)
            Pi_low = f_low / A * const.bar_per_md_pressure
            Pi_high = f_high / A * const.bar_per_md_pressure
            Pi_low_err = f_low_err / A * const.bar_per_md_pressure
            Pi_high_err = f_high_err / A * const.bar_per_md_pressure
            df['Pi_low'][(system['name'], osmp_name, 'prod')] = Pi_low
            df['Pi_high'][(system['name'], osmp_name, 'prod')] = Pi_high
            df['Pi_low_err'][(system['name'], osmp_name, 'prod')] = Pi_low_err
            df['Pi_high_err'][(system['name'], osmp_name, 'prod')] = Pi_high_err

            fig, ax = plt.subplots(figsize=(10, 4))
            x = data_low['Time (ps)']
            ax.plot(x, data_low['y'])
            ax.plot(x, -data_high['y'])
            x = np.arange(len_block/2, len_block*n_blocks, len_block) * data_low['Time (ps)'][1]
            ax.plot(x, f_low_blocks)
            ax.plot(x, f_high_blocks)
            plt.show()

## get p_tot (Pres-XX, Pres-YY)

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            run_bash("gmx energy -f prod/ener.edr -o pressure.xvg <<< 'Pres-XX\nPres-YY'")
            data, _ = gt.xvg.load('pressure.xvg')
            run_bash("rm pressure.xvg")
            p_tot = 1/2 * (data['Pres-XX'].mean() + data['Pres-YY'].mean())
            df['p_tot'][(system['name'], osmp_name, 'prod')] = p_tot

## calc p_in and p_ex

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            p_tot = df['p_tot'][(system['name'], osmp_name, 'prod')]
            Pi_low = df['Pi_low'][(system['name'], osmp_name, 'prod')]
            Pi_high = df['Pi_high'][(system['name'], osmp_name, 'prod')] 
            Pi = (Pi_low + Pi_high) / 2
            # p_tot = p_in + p_ex
            # Pi = p_in - p_ex
            p_ex = 1/2 * (p_tot - Pi)
            p_in = p_ex + Pi
            df['p_ex'][(system['name'], osmp_name, 'prod')] = p_ex
            df['p_in'][(system['name'], osmp_name, 'prod')] = p_in

## calculate actual mole fraction

In [ ]:
# equi_time = 500  # ps

for system in systems:
    print(f"system {system['name']}")
    
    for osmp_nr, (osmp_name, osmp_method) in enumerate(osmp_methods.items()):
        print('  osmp_name', osmp_name)
        working_dir = os.path.join(system['name'], osmp_name)
          
        with WorkingDir(working_dir):
            data, header = gt.xvg.load("prod/size.xvg")
            data.columns = ['t', 'MET', 'SOL']
            data['x'] = data['MET'] / (data['MET'] + data['SOL'])
            x = data['x'].mean()
            x_err = data['x'].std()

            df['x'][(system['name'], osmp_name, 'prod')] = x
            df['x_err'][(system['name'], osmp_name, 'prod')] = x_err
          
            # inner regime
            data, header = gt.xvg.load("prod/size-inner.xvg")
            data.columns = ['t', 'MET', 'SOL']
            data['x'] = data['MET'] / (data['MET'] + data['SOL'])
            x = data['x'].mean()
            x_err = data['x'].std()

            df['x_inner'][(system['name'], osmp_name, 'prod')] = x
            df['x_inner_err'][(system['name'], osmp_name, 'prod')] = x_err

In [ ]:
df

## fit

In [ ]:
# polyfit first, then optimize

for fit, fit_f, fit_n in [('fx3', fx3, 3), ('fx4', fx4, 4)]:
    print(fit)
    for osmp_name in osmp_methods:
        print(osmp_name)
        rows = (slice(None), osmp_name, 'prod')
        x = df['x_inner'][rows]
        y = (df['Pi_low'][rows] + df['Pi_high'][rows]) / 2

        # leave out last point
        #x = x[:-1]
        #y = y[:-1]

        prefit_p = np.polyfit(x, y, fit_n)
        fit_p, _ = optimize.curve_fit(fit_f, x, y, p0=prefit_p[:-1])
        print(np.linalg.norm(fit_f(x, *fit_p) - y))
        df_fit.loc[('prod', osmp_name), fit] = fit_p

## fit (both k values)

In [ ]:
# fit osmp-xy-k500
# polyfit first, then f(x) = cx + bx² + ax³
for fit, fit_f, fit_n in [('fx3', fx3, 3), ('fx4', fx4, 4)]:
    rows = (slice(None), slice(None), 'prod')
    x = df['x_inner'][rows]
    y = (df['Pi_low'][rows] + df['Pi_high'][rows]) / 2

    # leave out last point
    #x = x[:-1]
    #y = y[:-1]

    prefit_p = np.polyfit(x, y, fit_n)
    fit_p, _ = optimize.curve_fit(fit_f, x, y, p0=prefit_p[:-1])
    df_fit.loc[('prod', 'both'), fit] = fit_p

In [ ]:
df_fit

In [ ]:
df_fit.loc[('prod', 'both'), 'fx3']

## plot

In [ ]:
# Literature data: Kohns et al 2017, different methanol forcefield, different osm. pres. method
lit_x = [0.8779, 0.7901, 0.5098, 0.2235, 0.0407]
lit_x_err = [0.0008, 0.0008, 0.0007, 0.0004, 0.0001]
lit_y = [2180, 1409, 569, 258, 53.6]
lit_y_err = [5, 4, 4, 2, 0.9]

In [ ]:
cmap = plt.get_cmap('rainbow')
fig, ax = plt.subplots(figsize=(4.77, 3))
axins = inset_axes(ax, width="50%", height="40%", loc='upper left')
for i, osmp_name in enumerate(osmp_methods):
    for axi in [ax, axins]:
        rows = (slice(None), osmp_name, 'pre')
        axi.errorbar(df['x_inner'][rows], df['Pi_low'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_low_err'][rows],
                    color=cmap((i+2)/4), label=osmp_name + ' low inner', linestyle='')
        axi.errorbar(df['x_inner'][rows], df['Pi_high'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_high_err'][rows],
                    color=cmap((i+2)/4+0.1), label=osmp_name + ' high inner', linestyle='')
        fit_x = np.arange(0, 0.7, 0.01)
        fit_y = fx3(fit_x, *df_fit.loc[('pre', osmp_name), 'fx3'])
        axi.plot(fit_x, fit_y, color=cmap((i+2)/4), linestyle='-.', zorder=10, label=osmp_name + ' fit pre')

        rows = (slice(None), osmp_name, 'prod')
        axi.errorbar(df['x_inner'][rows], df['Pi_low'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_low_err'][rows],
                    color=cmap(i/4), label=osmp_name + ' low inner', linestyle='')
        axi.errorbar(df['x_inner'][rows], df['Pi_high'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_high_err'][rows],
                    color=cmap(i/4+0.1), label=osmp_name + ' high inner', linestyle='')
        x = df['x_inner'][rows]
        fit_x = np.arange(0, 0.7, 0.01)
        fit_y = fx4(fit_x, *df_fit.loc[('prod', osmp_name), 'fx4'])
        axi.plot(fit_x, fit_y, color=cmap(i/4), linestyle='-.', zorder=10, label=osmp_name + ' fit')
ax.errorbar(lit_x, lit_y, xerr=lit_x_err, yerr=lit_y_err, linestyle=':', label='Kohns et al')
axins.errorbar(lit_x, lit_y, xerr=lit_x_err, yerr=lit_y_err, linestyle=':', label='Kohns et al')
ax.legend(loc='upper right')
ax.set_xlim(0)
ax.set_ylim(0)
axins.set_xlim(0, 0.2)
axins.set_ylim(0, 400)
ax.set_xlabel('x(MET)')
ax.set_ylabel('Π in bar')
#ax.set_xlim(0, 0.2)
#ax.set_ylim(0, 400)
fig.savefig("figures/Pi.png", dpi=150)
plt.show()

In [ ]:
from cycler import cycler

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
colors = ['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B']
mpl_rc = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 3.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    'axes.prop_cycle': (
        cycler(color=colors)
        + cycler(ls=['-', '--', ':', (0, (5, 1)), '-.'])
    ),
}


with mpl.rc_context(rc=mpl_rc):
    df['Pi'] = (df['Pi_low'] + df['Pi_high']) / 2
    df['Pi_err'] = (df['Pi_low_err'] + df['Pi_high_err']) / 2 + np.abs(df['Pi_low'] - df['Pi_high'])
    fig, ax = plt.subplots(figsize=(4.77/2, 2.0), constrained_layout=True)
    axins = inset_axes(ax, width="50%", height="35%", bbox_to_anchor=(.08, .52, 1.2, 1.2), bbox_transform=ax.transAxes, loc=3)
    for i, osmp_name in enumerate(osmp_methods):
        osmp_key = r'$k_\mathrm{w}$=' + osmp_name.split('-')[-1][1:]
        for axi in [ax, axins]:
            """
            rows = (slice(None), osmp_name, 'pre')
            line, _, _ = axi.errorbar(df['x_inner'][rows], df['Pi'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_err'][rows],
                                      color=colors[1], label=osmp_key + ', pre.', linestyle='', fmt='.D'[i])
            fit_x = np.arange(0, 0.7, 0.01)
            fit_y = fx3(fit_x, *df_fit.loc[('pre', osmp_name), 'fx3'])
            #axi.plot(fit_x, fit_y, color=line.get_color(), linestyle=':', zorder=10) #, label=osmp_key + ' fit pre')
            """
            rows = (slice(None), osmp_name, 'prod')
            line, _, _ = axi.errorbar(df['x_inner'][rows], df['Pi'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_err'][rows],
                                      color=colors[1], label=osmp_key + '', linestyle='', fmt='.D'[i])
            x = df['x_inner'][rows]
            fit_x = np.arange(0, 0.7, 0.01)
            fit_y = fx3(fit_x, *df_fit.loc[('prod', osmp_name), 'fx3'])
            #axi.plot(fit_x, fit_y, color=line.get_color(), linestyle='--', zorder=10) #, label=osmp_key + ' fit prod')
    for axi in [ax, axins]:
        fit_x = np.arange(0, 0.7, 0.01)
        fit_y = fx3(fit_x, *df_fit.loc[('pre', 'both'), 'fx3'])
        #axi.plot(fit_x, fit_y, color=colors[1], linestyle=':', zorder=10) #, label=osmp_key + ' fit pre')
        fit_y = fx3(fit_x, *df_fit.loc[('prod', 'both'), 'fx3'])
        axi.plot(fit_x, fit_y, color=colors[4], linestyle=':', label=r'$\Pi_\mathrm{fit}$')
    for axi in (ax, axins):
        axi.errorbar(lit_x, lit_y, xerr=lit_x_err, yerr=lit_y_err, linestyle='-.', fmt='x', label='Kohns et al.', color='k', zorder=100)
    #ax.legend(loc=(0.01, 0.15))
    #ax.legend(loc=(-0.01, 0.46))
    # sort legend
    handles, labels = ax.get_legend_handles_labels()
    # sort both labels and handles by labels
    labels, handles = zip(*sorted(zip(labels, handles), key=lambda t: t[0], reverse=False))
    #order = [3, 1, 4, 2, 5, 0]
    order = [2, 1, 0, 3]
    handles, labels = [handles[idx] for idx in order], [labels[idx] for idx in order]
    ax.legend(handles, labels, loc='center left', bbox_to_anchor=(0.05, 0.70))
    #ax.legend(loc='center left', bbox_to_anchor=(-0.04, 0.74))
    ax.set_xlim(0, 0.72)
    ax.set_ylim(0)
    axins.set_xlim(0, 0.2)
    axins.set_ylim(0, 400)
    ax.set_xlabel(r'$x$(methanol)')
    ax.set_ylabel(r'$\Pi$ in bar')
    #ax.set_xlim(0, 0.2)
    #ax.set_ylim(0, 400)
    axins.remove()
    plt.show()
    fig.savefig("figures/osmp-results.pdf", dpi=fig.dpi)

In [ ]:
run_bash("cp figures/osmp-results.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

In [ ]:
# water pressure outside slab vs. concentration
cmap = plt.get_cmap('rainbow')

fig, ax = plt.subplots(figsize=(6, 4))
for i, osmp_name in enumerate(osmp_methods):
    osmp_key = osmp_name.split('-')[-1]
    #rows = (slice(None), osmp_name, 'pre')
    #ax.plot(df['x_inner'][rows], df['p_ex'][rows], color=cmap((i+2)/4), label=osmp_key + ' pre', marker='x', linestyle=':')
    #rows = (slice(None), osmp_name, 'prod')
    #ax.plot(df['x_inner'][rows], df['p_ex'][rows], color=cmap(i/4), label=osmp_key + ' prod ex', marker='D', linestyle=':')
    rows = (slice(None), osmp_name, 'pre')
    ax.plot(df['x_inner'][rows], df['p_tot'][rows], color=cmap((i+2)/4), label=osmp_key + ' pre tot', marker='<', linestyle=':')
    rows = (slice(None), osmp_name, 'prod')
    ax.plot(df['x_inner'][rows], df['p_tot'][rows], color=cmap(i/4), label=osmp_key + ' prod tot', marker='>', linestyle=':')
    #rows = (slice(None), osmp_name, 'prod')
    #ax.plot(df['x_inner'][rows], df['p_in'][rows], color=cmap(i/4), label=osmp_key + ' prod in', marker='^', linestyle=':')
ax.legend()
ax.set_title('outside pressure')
ax.set_xlabel('x(MET)')
ax.set_ylabel('p_ex in bar')
#ax.set_xlim(0)
#ax.set_ylim(0)
fig.savefig("figures/p_ex.png", dpi=150)
plt.show()

In [ ]:
# in slab pressure
cmap = plt.get_cmap('rainbow')

fig, ax = plt.subplots(figsize=(6, 4))
for i, osmp_name in enumerate(osmp_methods):
    osmp_key = osmp_name.split('-')[-1]
    rows = (slice(None), osmp_name, 'pre')
    #ax.errorbar(df['x'][rows], df['Pi_low'][rows], xerr=df['x_err'][rows], yerr=df['Pi_low_err'][rows],
                #color=cmap(i/4), label=osmp_name + ' low', linestyle='')
    #ax.errorbar(df['x'][rows], df['Pi_high'][rows], xerr=df['x_err'][rows], yerr=df['Pi_high_err'][rows],
                #color=cmap(i/4), label=osmp_name + ' high', linestyle='')
    ax.plot(df['x'][rows], df['p_in'][rows], color=cmap((i+2)/4), label=osmp_key + ' pre', marker='x', linestyle=':')
    rows = (slice(None), osmp_name, 'prod')
    ax.plot(df['x'][rows], df['p_in'][rows], color=cmap(i/4), label=osmp_key + ' prod', marker='D', linestyle=':')
ax.legend()
ax.set_title('inside pressure')
ax.set_xlabel('x(MET)')
ax.set_ylabel('p_in in bar')
#ax.set_xlim(0)
#ax.set_ylim(0)
fig.savefig("figures/p_in.png", dpi=150)
plt.show()

## save and load data frame

In [ ]:
df.to_pickle('df.pkl')
df_fit.to_pickle('df_fit.pkl')

In [ ]:
df = pd.read_pickle('df.pkl')
df_fit = pd.read_pickle('df_fit.pkl')

In [ ]:
df

In [ ]:
df_fit

# Inverse CG

## prepare inverse

In [ ]:
template_dir = os.path.abspath('template')

for mix_name, mix in mixtures.items():
    for system in mix['systems']:
        print(f"system {system['name']}")

        with WorkingDir(system['name']):
        # make dirs and copy template files
          
            for cg_method in cg_methods:
                print(f"  cg_name {cg_method['name']}")
                cg_name = cg_method['name']
                method_base = cg_method['method']
                alc_name = system['moltypes'][1]['name']
                run_bash(f"mkdir -p {cg_name}")
                run_bash(f"cp {template_dir}/{cg_name}/settings.xml {cg_name}/settings.xml")
                run_bash(f"cp {template_dir}/cg/{mix_name}/grompp-{cg_name}.mdp {cg_name}/grompp.mdp")
                run_bash(f"cp {template_dir}/table.xvg {cg_name}/table.xvg")
              
                # prepare initial configuration
                # volume from average of prod
                run_bash("gmx energy -f prod/ener.edr -o vol.xvg <<< 'Volume'")
                data, _ = gt.xvg.load("vol.xvg")
                run_bash("rm vol.xvg")
                volume_aa = data['Volume'].mean()
                # number of molecules
                nmols_aa = system['top'].moltypes()[1].nmols
                nmols_cg = mix['nmols_cg']
                # copy and check gro file
                run_bash(f"cp {template_dir}/cg/{mix_name}/conf-{nmols_cg}.gro temp.gro")
                box_cur, y, z = gt.gro.get_box(f"temp.gro")
                assert box_cur == y == z
                # calculate cg box size
                box_tgt = (volume_aa * nmols_cg / nmols_aa)**(1/3)
                # scale box
                scale = box_tgt / box_cur
                run_bash(f"gmx editconf -scale {scale} -f temp.gro -o {cg_name}/conf.gro")

                # copy stuff from prod
                run_bash(f"cp prod/A-A.dist.new {cg_name}/A-A.dist.tgt")

                # get pressure
                if cg_method['p-constr'] == 'osmp':
                    pressure = np.round(fx3(system['x'], *df_fit.loc[('prod', 'both'), 'fx3']))
                elif cg_method['p-constr'] == None:
                    pressure = 'none'
                else:
                    raise Exception('unknown p-constr')
                      
              
                # get density
                box_x, box_y, box_z = gt.gro.get_box(f"{cg_name}/conf.gro")
                density = mix['nmols_cg'] / (box_x * box_y * box_z)
                #print(mix['nmols_cg'], (box_x, box_y, box_z), density)
              
                # hncgn settings
                tree = ET.parse(f'{cg_name}/settings.xml')
                root = tree.getroot()
                root.find('non-bonded').find('max').text = str(mix['g_end'])
                root.find('non-bonded').find('step').text = str(mix['step'])
                root.find('inverse').find('kBT').text = str(const.k_gro * system['temperature'])
                root.find('inverse').find('iie').find('densities').text = str(density)
                root.find('inverse').find('iie').find('cut_off').text = str(system['cut_off'])
                root.find('inverse').find('iie').find('cut_gn').text = str(system['g_end'])
                root.find('inverse').find('iie').find('initial_guess').find('closure').text = cg_method['init']
                root.find('inverse').find('iie').find('pressure_constraint').text = str(pressure)
                root.find('inverse').find('gromacs').find('table_end').text = str(mix['g_end']
                                               + float(gt.mdp.get_parameter(f"{cg_name}/grompp.mdp", 'table-extension'))
                                               + 0.1)
                root.find('inverse').find('iterations_max').text = '20'
                tree.write(f'{cg_name}/settings.xml')

                # cut off
                for tag in ('rlist', 'rcoulomb', 'rvdw'):
                    gt.mdp.set_parameter(f"{cg_name}/grompp.mdp", tag, system['cut_off'])

                # run length
                print(np.round(40000 / system['x']))
                gt.mdp.set_parameter(f"{cg_name}/grompp.mdp", 'nsteps', 10000 + int(np.round(40000 / system['x'])))

                # set temperature
                gt.mdp.set_parameter(f"{cg_name}/grompp.mdp", 'ref-t', system['temperature'])

                # make index file
                run_bash(f"gmx make_ndx -f {cg_name}/conf.gro -o {cg_name}/index.ndx << EOF\na A\nq\nEOF")
                run_bash(f"rm -f {cg_name}/\#*")
              
                # generate topology
                nmols_cg = mix['nmols_cg']
                mol_name = mix['moltypes'][1]['name']
                mol_mass = system['top'].moltypes()[1].mols()[0].mass
                topol = f"""[ defaults ]
;nbfunc  comb-rule  gen-pairs  fudgeLJ  fudgeQQ
1        1          no         1.0      1.0

[ atomtypes ]
;atomname  mass        charge  type  sigma  epsilon
A          {mol_mass}  0.0     A     1.0    1.0

[ moleculetype ]
;molname    nrexcl
{mol_name}  1

[ atoms ]
;id  at-type  res-nr  res-name    at-name  cg-nr  charge
1    A        1       {mol_name}  A        1      0

[ system ]
coarse grained implicit alcohol

[ molecules ]
{mol_name}  {nmols_cg}
"""
                with open(f"{cg_name}/topol.top", 'w') as f:
                    f.write(topol)

## run inverse CG on cluster

In [ ]:
methods_to_run = [
    'p-hncgn-1',
    #'p-hncgn-2',
    'p-hncgn-3',
    #'p-hncgn-4',
]
systems_to_run = systems

for system in systems_to_run:
    print("system", system['name'])
    
    for method in methods_to_run:
        print("method", method)
    
        working_dir = os.path.join(system['name'], method)
        remote_dir = os.path.join(remote_dir_base, system['name'], method)

        with WorkingDir(working_dir):
            # mkdir
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

            # copy simulation files to remote
            filelist = ["A-A.dist.tgt", "conf.gro", "grompp.mdp", "index.ndx", "settings.xml", "table.xvg", "topol.top"]
            gt.remote.push_files(filelist, remote_host, remote_dir)

            # commands to be run on compute nodes
            script = """#!/bin/bash
#SBATCH --job-name=votca
#SBATCH --exclusive
#SBATCH --time=24:00:00
#SBATCH --partition=enzo

set -eo pipefail
shopt -s expand_aliases
alias gmx="gmx -quiet"

module purge
spack load /qmpnnzb  # gromacs@2019.5 ~mpi simd=SSE2
spack load /e4wa6u5  # fftw@3.3.8~mpi~openmp~pfft_patches precision=double,float
spack load /p2rbc3m  # boost@1.72~python
source /home/mbernhardt/software/votca/bin/VOTCARC.bash
source /home/mbernhardt/software/miniconda3/etc/profile.d/conda.sh
conda activate

ln -sf $JOBTMP jobtmp
csg_inverse --options settings.xml
unlink jobtmp
"""

            jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)

## check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

## copy results from cluster

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    remote_dir = os.path.join(remote_dir_base, system['name'])

    with WorkingDir(system['name']):
        filelist = ["*/step_*/{*.dist.new,*.pot.new,*.pot.cur,*.dpot.new,ener.edr}",
                   "*/step_*/*.dist.tgt"]
        exclude = "*traj*"
        gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)

## equilibration check

In [ ]:
# pressure from RDF and U
# force from average of forward and backward derivative of U
def calc_pressure_bar1(r, g, U, rho, kBT, cut_off, g_min):
    delta_r = r[1] - r[0]
    core_end = np.where(g > g_min)[0][0]
    cut_off = np.searchsorted(r, cut_off)
    main = slice(core_end, cut_off+2)
    uprime1 = np.concatenate((np.diff(U[main]), [0])) / delta_r
    uprime2 = np.concatenate(([0], np.diff(U[main]))) / delta_r
    uprime = (uprime1 + uprime2) / 2
    #uprime = uprime1
    p_rdf = rho*kBT - 2/3 * np.pi * rho**2 * delta_r * np.sum(uprime * g[main] * r[main]**3)
    return p_rdf * 1e28 * const.u  # conversion from md units to bar

# read votca table
def readin_table(filename):
    table_dtype = {'names': ('x', 'y', 'y_flag'),
                   'formats': ('f', 'f', 'S1')}
    x, y, y_flag = np.loadtxt(filename, dtype=table_dtype, comments=['#', '@'], unpack=True)
    return x, y, y_flag

def get_target_pressure(settings_filename):
    tree = ET.parse(settings_filename)
    root = tree.getroot()
    p = float(root.find('inverse').find('iie').find('pressure_constraint').text)
    return p

In [ ]:
cmap = plt.get_cmap('rainbow')

methods_to_show = []
#methods_to_show += ['hncgn-1']
#methods_to_show += ['hncgn-2']
#methods_to_show += ['p-hncgn-1']
methods_to_show += ['p-hncgn-2']
#methods_to_show += ['p-hncgn-3']
#methods_to_show += ['p-hncgn-4']
systems_to_show = systems
#systems_to_show = systems[2:3]

for system in systems_to_show:
    print("system", system['name'])
    
    run_bash("rm -f energy-temp.xvg")
    for method in methods_to_show:
        print("method", method)
        working_dir = os.path.join(system['name'], method)
        
        fig, (ax0, ax1, ax2) = plt.subplots(nrows=1, ncols=3, figsize=[18, 2])

        with WorkingDir(working_dir):
            ener_files = sorted(glob.glob('step_*/ener.edr'))
            if ener_files == []:
                print('.. no ener.edr files ..')
                continue
            max_step = int(re.search('step_(\d+)', ener_files[-1]).group(1))
            if max_step > 8:
                #ener_files = ener_files[::max_step/8]
                ener_files = [ener_files[i-1] for i in np.floor(np.linspace(1, max_step, num=8, endpoint=True)).astype(int)]
            steps = []
            pressures = []
            pressures_std = []
            for ener_file in ener_files:
                if os.stat(ener_file).st_size == 0:
                    continue
                step = int(re.search('step_(\d+)', ener_file).group(1))
                run_bash(f"gmx energy -f {ener_file} -o /tmp/energy-temp.xvg <<< 'Temperature\nPressure'")
                data, header = gt.xvg.load("/tmp/energy-temp.xvg")
                steps.append(step)
                pressure = data[data['Time (ps)'] > 10]['Pressure'].mean()
                pressure_err = data[data['Time (ps)'] > 10]['Pressure'].std()
                pressures.append(pressure)
                pressures_std.append(pressure_err)
                run_bash(f"rm -f /tmp/energy-temp.xvg")
                ax0.plot(data['Time (ps)'], data['Temperature'], label=f"step {step}", color=cmap(step/max_step))
                ax1.plot(data['Time (ps)'], data['Pressure'], label=f"step {step}", color=cmap(step/max_step))
            ax2.errorbar(steps, pressures, pressures_std, label='pressure cur')
            # plot target pressure
            try:
                p_tgt = get_target_pressure('settings.xml')
                ax2.axhline(p_tgt, linestyle=':', color='darkgreen')
            except:
                pass

        ax0.set_title("Temperature")
        ax1.set_title("Pressure")
        ax2.set_title("Pressure vs. step")
        ax0.legend(loc='center right')
        ax2.legend()
        fig.tight_layout()    
        plt.show()

## dist, dU, U

In [ ]:
cmap = plt.get_cmap('rainbow')

#methods_to_show = ['hncgn-1']
#methods_to_show = ['hncgn-2']
methods_to_show = []
#methods_to_show += ['p-hncgn-1']
methods_to_show += ['p-hncgn-2']
#methods_to_show += ['p-hncgn-3']
#methods_to_show += ['p-hncgn-4']
systems_to_show = systems
#systems_to_show = systems[2:3]
comparisons_to_show = []
comparisons_to_show = ['hncgn-1/step_010']

for system in systems_to_show:
    print("system", system['name'])
    for method in methods_to_show:
        print("method", method)
        working_dir_parent = os.path.abspath(system['name'])
        working_dir = os.path.join(system['name'], method)
    
        
        with WorkingDir(working_dir):
            if len(glob.glob('step_*/')) <= 1:
                continue
                
            fig, (ax0, ax1, ax2) = plt.subplots(nrows=1, ncols=3, figsize=[13, 4])
            axins0 = inset_axes(ax0, width="50%", height="40%", loc='upper right')
                
            # plot g(r)
            dist_files = sorted(glob.glob('step_*/A-A.dist.new'))
            max_step = int(re.search('step_(\d+)', dist_files[-1]).group(1))
            dist_files = dist_files[::max(max_step//8, 1)]
            _, dist_tgt_g, _ = readin_table(f"step_001/A-A.dist.tgt")
            g_std = []
            for dist_file in dist_files:
                step = int(re.search('step_(\d+)', dist_file).group(1))
                dist_r, dist_g, dist_flag = readin_table(dist_file)
                #print(dist_g[40:50])
                ax0.plot(dist_r, dist_g, label=f"step {step}", color=cmap(step/max_step))
                ax0.set_title("g(r)")
                g_std.append((step, np.sqrt(1/max(dist_r) * np.trapz(x=dist_r, y=(dist_g - dist_tgt_g)**2))))
            # rdf convergence inset
            line = axins0.plot(*zip(*g_std))

            # plot dU(r)  
            dpot_files = sorted(glob.glob('step_*/A-A.dpot.new'))
            dpot_files = dpot_files[::max(max_step//8, 1)]
            for dpot_file in dpot_files:
                step = int(re.search('step_(\d+)', dpot_file).group(1))
                dpot_r, dpot_dU, dist_flag = readin_table(dpot_file)
                ax1.plot(dpot_r, dpot_dU, '.-', label=f"step {step}", color=cmap(step/max_step))
                #ax1.plot([0.88, 0.88], [-100, 100], '--')
                #print(dpot_r[40:50])
                #print(dpot_dU[40:50])
                ax1.set_title("ΔU(r)")
                ax1.set_ylim((-1, 1))
                #ax1.set_ylim((-100, 100))

            # plot U(r)
            pot_files = sorted(glob.glob('step_*/A-A.pot.new'))
            pot_files = pot_files[::max(max_step//8, 1)]
            for pot_file in pot_files:
                step = int(re.search('step_(\d+)', pot_file).group(1))
                pot_r, pot_U, dist_flag = readin_table(pot_file)
                ax2.plot(pot_r, pot_U, label=f"step {step}", color=cmap(step/max_step))
                ax2.set_ylim((-2, 5))
                #ax2.set_ylim((-0.2, 0.2))
                ax2.set_title("U(r)")

            # plot target g(r)
            dist_r, dist_g, dist_flag = readin_table("A-A.dist.tgt")
            ax0.plot(dist_r, dist_g, label="target", color='k', linestyle='--')
                
            # plot comparisons
            for comparison in comparisons_to_show:
                with WorkingDir(working_dir_parent):
                    pot_r, pot_U, pot_flag = readin_table(f"{comparison}/A-A.pot.new")
                ax2.plot(pot_r, pot_U, label=comparison, linestyle='--')

            ax0.legend(loc='lower right')
            ax1.legend() #loc='upper right')
            ax2.legend(loc='upper right')
            ax2.grid()
            for ax in (ax1, ax2):
                ax.set_xlim((0.0, system['cut_off'] + 0.2))
                ax.set_xlabel("r / nm")
                #ax.grid()
            for ax in (ax1, ax2):
                ax.set_ylabel("U in kJ mol¯¹")
            ax0.set_xlim((0.0, system['g_end'] + 0.2))
            ax0.set_xlabel("r / nm")
                
            g_start = dist_r[np.where(dist_g > 1e-10)[0][0]]
            #ax0.set_xlim((0.8*g_start, 1.2*g_start))
            #ax1.set_xlim((0.8*g_start, 1.2*g_start))
            #ax2.set_xlim((0.8*g_start, 1.2*g_start))
            #ax0.set_ylim((0.0, 0.1))
            
        fig.tight_layout()    
        fig.savefig(f"figures/{method}_{system['name']}.png", dpi=150)
        plt.show()

## paper plot spikes

In [ ]:
from cycler import cycler

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
colors = ['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B']
mpl_rc = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'legend.labelspacing': 0.5,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
}

with plt.rc_context(mpl_rc):
    fig, ax = plt.subplots(figsize=(4.77/2, 2), constrained_layout=True)
    #ax_g = ax.twinx()
    for cg_ndx, sys_ndx, step in ((5, 0, '001'), (5, 1, '002')):
    #for cg_ndx, sys_ndx, step in ((5, 2, '002'),):
        cg_method = cg_methods[cg_ndx]
        system = systems[sys_ndx]
        print(cg_method['name'], system['name'])
        folder = 'step_' + str(step)
        #folder = 'step_001'
        working_dir = os.path.join(system['name'], cg_method['name'], folder)
        with WorkingDir(working_dir):
            r, g_k, _ = readin_table('A-A.dist.new')
            _, g_tgt, _ = readin_table('A-A.dist.tgt')
            _, u_k, _ = readin_table('A-A.pot.cur')
            _, u_kp1, _ = readin_table('A-A.pot.new')
            _, Du, _ = readin_table('A-A.dpot.new')


        #if step == '002':
            #ax_g.plot(r, g_tgt, linestyle='--', label=r'$g_\mathrm{tgt}$', color=colors[1])
            #ax_g.plot(r, g_k, linestyle=':', label=r'$g_k$', color=colors[0])
        #ax.plot(r, u_k, linestyle='-', label=r'$u_k$', color=colors[int(step)])
        #ax.plot(r, u_kp1, linestyle='-', label=r'$u_{k+1}$', color=colors[int(step)])
        ax.plot(r, Du, linestyle='-', label=f"x={system['x']}\niter.={int(step)}", color=colors[int(step)])

    fig.legend(loc=(0.40, 0.60))
    ax.set_xlabel(r'$r$ in nm')
    ax.set_ylabel(r'$\Delta u$ in kJ/mol')
    ax.set_xlim(0.0, 1.4)
    ax.set_ylim(-0.3, 0.9)
    #ax.set_ylim(-0.03, 0.03)
    fig.savefig("figures/pot-spike.pdf", dpi=300)
    plt.show()

In [ ]:
run_bash("cp figures/pot-spike.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

## create DataFrame

In [ ]:
# build empty DataFrame
iterables = [[system['name'] for system in systems],
             [cg_method['name'] for cg_method in cg_methods]]
index = pd.MultiIndex.from_product(iterables, names=['system', 'cg_method'])
df_cg = pd.DataFrame(index=index, columns=["p", "p_err"], dtype=np.float64)
df_cg.head()

## read pressure

In [ ]:
equi_time = 10

for system in systems:
    print("system", system['name'])
    
    run_bash("rm -f energy-temp.xvg")
    for cg_method in cg_methods:
        print("method", cg_method['name'])
        working_dir = os.path.join(system['name'], cg_method['name'])
        
        with WorkingDir(working_dir):
            ener_files = sorted(glob.glob('step_*/ener.edr'))
            if ener_files == []:
                continue
            pressures = []
            pressures_err = []
            last_ener_file = ener_files[-2]
            run_bash(f"gmx energy -f {last_ener_file} -o /tmp/energy-temp.xvg <<< 'Pressure'")
            data, header = gt.xvg.load("/tmp/energy-temp.xvg")
            run_bash(f"rm -f /tmp/energy-temp.xvg")
            pressure = data[data['Time (ps)'] > 10]['Pressure'].mean()
            pressure_err = data[data['Time (ps)'] > 10]['Pressure'].std()
            index = (system['name'], cg_method['name'])
            df_cg.loc[index, 'p'] = pressure
            df_cg.loc[index, 'p_err'] = pressure_err

In [ ]:
df_cg

In [ ]:
print(df_cg.loc[(slice(None), 'p-hncgn-2'), slice(None)].to_latex())

## plot pressure

In [ ]:
from cycler import cycler

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
colors = ['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B']
mpl_rc = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'legend.labelspacing': 0.5,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 3.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
}

label_dict = {
    'hncgn-1': 'HNCGN',
    'p-hncgn-2': 'p-HNCGN',
}

cg_methods_to_show = []
cg_methods_to_show += [cg_methods[0]]
cg_methods_to_show += [cg_methods[3]]

with plt.rc_context(mpl_rc):
    fig, ax = plt.subplots(figsize=(4.77/2, 2), constrained_layout=True)
    for i, cg_method in enumerate(cg_methods_to_show):
        print(cg_method['name'])
        rows = (slice(None), cg_method['name'])
        x = [system['x'] for system in systems]
        y = df_cg.loc[rows, 'p']
        y_err = df_cg.loc[rows, 'p_err']
        with mpl.rc_context(rc={'errorbar.capsize': 5}):
            label = label_dict[cg_method['name']]
            marker = ['s', 'D', 'x', '<', '>', 'o'][i]
            color = colors[2*i]
            ax.errorbar(x, y, yerr=y_err, linestyle='', label=label, marker=marker, color=color)
        #ax.plot(df['x_inner'][rows], df['p_ex'][rows], color=cmap((i+1)/4), label=osmp_name + ' p_tot', marker='x', linestyle=':')

    # target
    fit_x = np.arange(0, 0.95, 0.01)
    fit_y = fx3(fit_x, *df_fit.loc[('prod', 'both'), 'fx3'])
    ax.plot(fit_x, fit_y, color=colors[4], linestyle=':', zorder=-1, label=r'$\Pi_\mathrm{fit}$', marker='')

    ax.legend(loc=(0.08, 0.55))
    ax.set_xlim(0)
    ax.set_ylim(0, 10000)
    ax.set_xlabel('x(methanol)')
    ax.set_ylabel('p in bar')
    fig.savefig("figures/pressures.pdf", dpi=300)
    plt.show()

In [ ]:
fit_y_cg = fx3(np.array([0.05, 0.1, 0.2, 0.4, 0.6, 0.8, 0.9]), *df_fit.loc[('prod', 'both'), 'fx3'])
print(fit_y_cg)

In [ ]:
run_bash("cp figures/pressures.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

## plot dist and pot

In [ ]:
cmap = plt.get_cmap('turbo')

methods_to_show = []
methods_to_show += ['hncgn-1']
methods_to_show += ['hncgn-2']
methods_to_show += ['p-hncgn-1']
methods_to_show += ['p-hncgn-2']
systems_to_show = systems

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
colors = ['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B']
mpl_rc = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
}

with plt.rc_context(mpl_rc):
    for method in methods_to_show:
        print("method", method)

        fig, (ax0, ax1) = plt.subplots(nrows=2, ncols=1, figsize=(4.77/2, 4), sharex='col',
                                      gridspec_kw = {'wspace':0, 'hspace':0})

        for i, system in enumerate(systems_to_show):
            print("system", system['name'])
            working_dir_parent = os.path.abspath(system['name'])
            working_dir = os.path.join(system['name'], method)


            with WorkingDir(working_dir):
                if len(glob.glob('step_*/')) <= 1:
                    continue


                # plot g(r)
                dist_file = 'step_010/A-A.dist.new'
                step = int(re.search('step_(\d+)', dist_file).group(1))
                dist_r, dist_g, dist_flag = readin_table(dist_file)
                #print(dist_g[40:50])
                ax0.plot(dist_r, dist_g, label=f"{system['x']:.2f}", color=cmap(i/7))

                # plot U(r)
                pot_file = 'step_010/A-A.pot.cur'
                step = int(re.search('step_(\d+)', pot_file).group(1))
                pot_r, pot_U, dist_flag = readin_table(pot_file)
                ax1.plot(pot_r, pot_U, label=f"{system['x']:.2f}", color=cmap(i/7))
                ax1.set_ylim((-1.5, 4.8))
                #ax1.set_ylim((-0.2, 0.2))

        ax0.set_ylabel(r"$g$")
        ax0.set_xlim((0.0, system['g_end']))
        ax1.legend(loc='upper right')
        ax1.set_xlim((0.0, system['cut_off']))
        ax1.set_xlabel("r / nm")
        ax1.set_ylabel(r"$u$ in kJ/mol")

        g_start = dist_r[np.where(dist_g > 1e-10)[0][0]]
        #ax0.set_xlim((0.8*g_start, 1.2*g_start))
        #ax1.set_xlim((0.8*g_start, 1.2*g_start))
        #ax2.set_xlim((0.8*g_start, 1.2*g_start))
        #ax0.set_ylim((0.0, 0.1))

        fig.tight_layout()    
        fig.savefig(f"figures/{method}-dist-and-pot.pdf", dpi=300)
        plt.show()

In [ ]:
run_bash("cp figures/p-hncgn-2-dist-and-pot.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

In [ ]:
cmap = plt.get_cmap('rainbow')

fig, ax = plt.subplots(figsize=(18, 8))
axins = inset_axes(ax, width="50%", height="40%", loc='upper left')
for axi in [ax, axins]:
    for i, osmp_name in enumerate(osmp_methods):
        rows = (slice(None), osmp_name, 'pre')
        axi.errorbar(df['x_inner'][rows], df['Pi_low'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_low_err'][rows],
                    color=cmap((i+2)/4), label=osmp_name + ' low inner', linestyle='')
        axi.errorbar(df['x_inner'][rows], df['Pi_high'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_high_err'][rows],
                    color=cmap((i+2)/4+0.1), label=osmp_name + ' high inner', linestyle='')
        fit_x = np.arange(0, max(x), 0.01)
        fit_y = fx4(fit_x, *df_fit.loc[('pre', osmp_name), 'fx4'])
        axi.plot(fit_x, fit_y, color=cmap((i+2)/4), linestyle='-.', zorder=10, label=osmp_name + ' fit pre')
        
        """
        rows = (slice(None), osmp_name, 'prod')
        axi.errorbar(df['x_inner'][rows], df['Pi_low'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_low_err'][rows],
                    color=cmap(i/4), label=osmp_name + ' low inner', linestyle='')
        axi.errorbar(df['x_inner'][rows], df['Pi_high'][rows], xerr=df['x_inner_err'][rows], yerr=df['Pi_high_err'][rows],
                    color=cmap(i/4+0.1), label=osmp_name + ' high inner', linestyle='')
        x = df['x_inner'][rows]
        fit_x = np.arange(0, max(x), 0.01)
        fit_y = fx3(fit_x, *df_fit.loc[('prod', osmp_name), 'fx3'])
        axi.plot(fit_x, fit_y, color=cmap(i/4), linestyle='-.', zorder=10, label=osmp_name + ' fit')
        """
        
    for cg_method in cg_methods:
        cg_name = cg_method['name']
        rows = (slice(None), cg_name)
        x = [system['x'] for system in systems]
        y = df_cg.loc[rows, 'p']
        y_err = df_cg.loc[rows, 'p_err']
        axi.errorbar(x, y, yerr=y_err, linestyle='-', label=cg_name)
ax.legend(loc='upper right')
ax.set_xlim(0)
ax.set_ylim(0)
axins.set_xlim(0, 0.2)
axins.set_ylim(0, 400)
#ax.set_xlim(0, 0.2)
#ax.set_ylim(0, 400)
plt.show()

In [ ]:
df_fit[]

# transferability test MD

## prepare transf

In [ ]:
template_dir = os.path.abspath('template')

for system in systems:
    print("system", system['name'])
          
    with WorkingDir(system['name']):
        # make dirs and copy template files
        run_bash("mkdir -p transf-tempf")
        
        # create folders
        for tempf in transf_tempf:
            run_bash(f"mkdir -p transf-tempf/aa/{tempf:.2f}/{{equi1,prod}}")
            for cg_method in transf_cg_methods:
                cg_name = cg_method['name']
                run_bash(f"mkdir -p transf-tempf/{cg_name}/topol")
                run_bash(f"mkdir -p transf-tempf/{cg_name}/{tempf:.2f}/{{equi1,prod}}")
            
        # copy/link topologies
        with WorkingDir("transf-tempf/aa"):
            run_bash("ln -snf ../../topol topol")
        for cg_method in transf_cg_methods:
            cg_name = cg_method['name']
            run_bash(f"cp -t transf-tempf/{cg_name}/topol {cg_name}/topol.top {cg_name}/table.xvg")
            run_bash(f"cp -t transf-tempf/{cg_name}/topol {cg_name}/settings.xml")
            run_bash(f"cp -t transf-tempf/{cg_name}/topol {cg_name}/index.ndx")
            run_bash(f"cp -t transf-tempf/{cg_name}/topol {cg_name}/step_010/table_A_A.xvg")
                
        # copy initial conf
        for tempf in transf_tempf:
            with WorkingDir(f"transf-tempf/aa/{tempf:.2f}"):
                run_bash("cp ../../../prod/confout.gro equi1/conf.gro")
            for cg_method in transf_cg_methods:
                cg_name = cg_method['name']
                with WorkingDir(f"transf-tempf/{cg_name}/{tempf:.2f}"):
                    run_bash(f"cp ../../../{cg_name}/step_010/confout.gro equi1/conf.gro")
                        
        # copy grompp
        for tempf in transf_tempf:
            with WorkingDir(f"transf-tempf/aa/{tempf:.2f}"):
                run_bash(f"cp {template_dir}/md-transf-tempf/aa/equi1.mdp equi1/grompp.mdp")
                run_bash(f"cp {template_dir}/md-transf-tempf/aa/prod.mdp prod/grompp.mdp")
            for cg_method in transf_cg_methods:
                cg_name = cg_method['name']
                with WorkingDir(f"transf-tempf/{cg_name}/{tempf:.2f}"):
                    run_bash(f"cp {template_dir}/md-transf-tempf/cg/equi1.mdp equi1/grompp.mdp")
                    run_bash(f"cp {template_dir}/md-transf-tempf/cg/prod.mdp prod/grompp.mdp")
                    
        # modify grompp
        for tempf in transf_tempf:
            with WorkingDir(f"transf-tempf/aa/{tempf:.2f}"):
                gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps', 30000)
                prod_run_length = int(8000 / system['top'].moltypes()[1].nmols * 10000)
                gt.mdp.set_parameter("prod/grompp.mdp",  'nsteps', prod_run_length)
                gt.mdp.set_parameter("equi1/grompp.mdp", 'ref-t', system['temperature'] * tempf)
                gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t', system['temperature'] * tempf)
            for cg_method in transf_cg_methods:
                cg_name = cg_method['name']
                with WorkingDir(f"transf-tempf/{cg_name}/{tempf:.2f}"):
                    gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps', 30000)
                    prod_run_length = int(8000 / system['top'].moltypes()[1].nmols * 10000)
                    gt.mdp.set_parameter("prod/grompp.mdp",  'nsteps', prod_run_length)
                    gt.mdp.set_parameter("equi1/grompp.mdp", 'ref-t', system['temperature'] * tempf)
                    gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t', system['temperature'] * tempf)
                    for tag in ('rlist', 'rcoulomb', 'rvdw'):
                        gt.mdp.set_parameter(f"equi1/grompp.mdp", tag, system['cut_off'])
                        gt.mdp.set_parameter(f"prod/grompp.mdp", tag, system['cut_off'])

## md aa on cluster

In [ ]:
for system in systems:
    print("system", system['name'])
          
    # push topol folder
    working_dir = system['name'] + f"/transf-tempf/aa/"
    remote_dir = os.path.join(remote_dir_base, working_dir)
    with WorkingDir(working_dir):
        run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")
        gt.remote.push_files(['topol'], remote_host, remote_dir, exclude="traj*")
        
    for tempf in transf_tempf:
        print("tempf", tempf)
        working_dir = system['name'] + f"/transf-tempf/aa/{tempf:.2f}"
        remote_dir = os.path.join(remote_dir_base, working_dir)
        
        with WorkingDir(working_dir):
            # mkdir
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

            # copy simulation files to remote
            filelist = ["equi1 prod"]
            gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

            # commands to be run on compute nodes
            script = """#!/bin/bash
#SBATCH --job-name=md
#SBATCH --exclusive
#SBATCH --time=48:00:00
#SBATCH --partition=enzo

set -euo pipefail
shopt -s expand_aliases
alias gmx="gmx -quiet"

module purge
spack load gromacs@2019 ~mpi simd=SSE2
spack load fftw~mpi
spack load /r3cs6fw  # boost
spack load py-numpy ^python@3
spack load python@3
source /home/mbernhardt/software/votca/bin/VOTCARC.bash

pushd equi1
gmx grompp -p ../../topol/topol.top
gmx mdrun
rm -f \#*
popd

pushd prod
gmx grompp -p ../../topol/topol.top -c ../equi1/confout.gro
gmx mdrun -x $JOBTMP/traj_comp.xtc
rm -f \#*
popd

ls -lh $JOBTMP

pushd prod
csg_stat --top ../../topol/special.tpr --options ../../topol/settings.xml --trj $JOBTMP/traj_comp.xtc \
--cg "../../topol/ALC-map.xml;../../topol/SOL-map.xml" --nt=24
rm -f \#*
popd
"""

            jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)

## md cg on cluster

In [ ]:
for system in systems:
    print("system", system['name'])
    for cg_method in transf_cg_methods:
        cg_name = cg_method['name']
        print('cg', cg_name)
          
        # push topol folder
        working_dir = system['name'] + f"/transf-tempf/{cg_name}"
        remote_dir = os.path.join(remote_dir_base, working_dir)
        with WorkingDir(working_dir):
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")
            gt.remote.push_files(['topol'], remote_host, remote_dir, exclude="traj*")
        
        for tempf in transf_tempf:
            print("tempf", tempf)
            working_dir = system['name'] + f"/transf-tempf/{cg_name}/{tempf:.2f}"
            remote_dir = os.path.join(remote_dir_base, working_dir)

            with WorkingDir(working_dir):
                # mkdir
                run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

                # copy simulation files to remote
                filelist = ["equi1 prod"]
                gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

                # commands to be run on compute nodes
                script = """#!/bin/bash
#SBATCH --job-name=md
#SBATCH --exclusive
#SBATCH --time=48:00:00
#SBATCH --partition=enzo

set -euo pipefail
shopt -s expand_aliases
alias gmx="gmx -quiet"

module purge
spack load gromacs@2019 ~mpi simd=SSE2
spack load fftw~mpi
spack load /r3cs6fw  # boost
spack load py-numpy ^python@3
spack load python@3
source /home/mbernhardt/software/votca/bin/VOTCARC.bash

pushd equi1
gmx grompp -p ../../topol/topol.top -n ../../topol/index.ndx
GMXLIB=../../topol gmx mdrun
rm -f \#*
popd

pushd prod
gmx grompp -p ../../topol/topol.top -c ../equi1/confout.gro -n ../../topol/index.ndx
GMXLIB=../../topol gmx mdrun -x $JOBTMP/traj_comp.xtc
rm -f \#*
popd

ls -lh $JOBTMP

pushd prod
csg_stat --top topol.tpr --options ../../topol/settings.xml --trj $JOBTMP/traj_comp.xtc --nt=24
rm -f \#*
popd
    """

                jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
                print(jobid)
                if jobid != None:
                    jobids.append(jobid)

## check job status

In [ ]:
# print status for each job
completed_jobids = []
for jobid in jobids:
    stati = gt.remote.check_slurm_job(jobid, remote_host)
    print(jobid, stati)
    if stati[-1] in ('FAILED', 'COMPLETED', 'CANCELLED', None):
        completed_jobids.append(jobid)

# remove jobids which are completed
jobids = [jobid for jobid in jobids if jobid not in completed_jobids]

## copy results from cluster

In [ ]:
for system in systems:
    print(f"system {system['name']}")

    working_dir = system['name'] + "/transf-tempf"
    remote_dir = os.path.join(remote_dir_base, working_dir)
        
    with WorkingDir(working_dir):
        exclude = "traj*"
        filelist = ["*/*/*/*.edr", "*/*/*/*/confout.gro", "*/*/*/*/topol.tpr", "*/*/prod/A-A.dist.new"]
        gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)

## equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    for res in [{'name': 'aa'}] + transf_cg_methods:
        cg_name = res['name']
        print(f"res {cg_name}")
        for tempf in transf_tempf:
            print("tempf", tempf)
            working_dir = system['name'] + f"/transf-tempf/{cg_name}/{tempf:.2f}"

            with WorkingDir(working_dir):
                #print("equilibration 1")
                #show_energy_graphs(["Temperature"], edr_file="equi1/ener.edr")
                print("production")
                show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")

## show RDFs

In [ ]:
linestyles = {'aa': '-', 'hncgn-1': ':', 'p-hncgn-1': '--'}
cmap = plt.get_cmap('plasma')

for system in systems:
    print(f"system {system['name']}")
          
    fig, ax = plt.subplots()
    axins = inset_axes(ax, width="50%", height="40%", loc='lower right')
    axins2 = inset_axes(ax, width="40%", height="30%", loc='upper right')
    axes = [ax, axins, axins2]
          
    fig2, ax2 = plt.subplots()
    for tempf in transf_tempf:
        print("tempf", tempf)
        color = cmap(4*tempf - 3.5)
          
        # load refdata
        working_dir = system['name'] + f"/transf-tempf/aa/{tempf:.2f}"
        with WorkingDir(working_dir):
            refdata, _ = gt.xvg.load("prod/A-A.dist.new")
          
        for res in [{'name': 'aa'}] + transf_cg_methods:
            cg_name = res['name']
            print(f"res {cg_name}")
          
            working_dir = system['name'] + f"/transf-tempf/{cg_name}/{tempf:.2f}"

            with WorkingDir(working_dir):
                data, header = gt.xvg.load("prod/A-A.dist.new")
                for a in axes:
                    a.plot(data[0], data[1], label=f"{cg_name} {tempf:.2f}",
                           linestyle=linestyles[cg_name], color=color)
          
            if cg_name != 'aa':
                ax2.plot(data[0], data[1] - refdata[1], label=f"{cg_name} {tempf:.2f}")

    ax.legend(title="temp. factor", loc='lower left')
    ax2.legend(title="temp. factor", loc='lower left')
    ax.set_xlim(-1, system['g_end'])
    ax.set_ylim(bottom=0)
    axins.set_xlim(0.4, 0.5)
    axins.set_ylim(1.3, 1.75)
    axins2.set_xlim(0.6 * system['g_end'], 1.01 * system['g_end'])
    axins2.set_ylim(0.995, 1.005)
    ax.set_xlabel("r in nm")
    ax.set_ylabel("g(r)")
    #axins.set_visible(False)
    axins2.set_visible(False)
    ax.set_title(system['name'])
    fig.tight_layout()
    fig.savefig(f"figures/transf-tempf-{system['name']}.png", dpi=150)
    plt.show()

## calculate RDF distance

In [ ]:
# build empty DataFrame for fits
iterables = [[system['name'] for system in systems],
             [res['name'] for res in transf_cg_methods],
             transf_tempf]
index = pd.MultiIndex.from_product(iterables, names=['system', 'cg', 'tempf'])
df_rdf = pd.DataFrame(index=index, columns=["msd"])
df_rdf.head()

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    for res in transf_cg_methods:
        cg_name = res['name']
        print(f"res {cg_name}")
          
        for tempf in transf_tempf:
            print("tempf", tempf)
          
            # load refdata
            working_dir = system['name'] + f"/transf-tempf/aa/{tempf:.2f}"
            with WorkingDir(working_dir):
                refdata, _ = gt.xvg.load("prod/A-A.dist.new")
          
            # load data and calc msd
            working_dir = system['name'] + f"/transf-tempf/{cg_name}/{tempf:.2f}"
            with WorkingDir(working_dir):
                try:
                    data, _ = gt.xvg.load("prod/A-A.dist.new")
                    msd = np.sum((data[1] - refdata[1])**2) * (data[0][1] - data[0][0])
                    df_rdf.loc[(system['name'], cg_name, tempf), 'msd'] = msd
                except:
                    print('no data')

In [ ]:
df_rdf

In [ ]:
fig, ax = plt.subplots(figsize=(5,3))
x = [system['x'] for system in systems]
fmts = ['o:', '<:']
cmap = plt.get_cmap("tab10")
colors = [cmap(0), cmap(1), cmap(2)]

for r, res in enumerate(transf_cg_methods):
    cg_name = res['name']
    #print(f"res {cg_name}")
    for t, tempf in enumerate(transf_tempf):
        #print("tempf", tempf)
        line = ax.plot(x, df_rdf.loc[(slice(None), cg_name, tempf), 'msd'],
                       fmts[r], color=colors[t], label=f"{cg_name} {tempf:.2f}")

ax.legend()
ax.set_ylim(bottom=0)
ax.set_xlabel("x(Methanol)")
ax.set_ylabel(r"$\int_0^{r_c} \left(g_\mathrm{CG}(r) - g_\mathrm{AA}(r)\right)^2 dr$")
fig.tight_layout()
fig.savefig(f"figures/transf-tempf-rdf-distance.png", dpi=150)
plt.show()